# <font color=red>DATA GATHERING I: MUSIC RELEASES AND THEIR GEOGRAPHICAL ORIGIN</font>

## <font color=blue>1) Artist information</font>

### Data from Musicbrainz.org

In [131]:
import pandas as pd
import numpy as np
#!pip install pygeocoder
#from pygeocoder import Geocoder #If you want to follow the geocoding later, you will need your own Google Maps API key
import reverse_geocoder #pip install reverse geocoder in console
import time
import tqdm
import warnings
warnings.filterwarnings('ignore')

In [132]:
artists= pd.read_csv('Musicbrainz/Tables_used/artist.txt',sep='\t', header=None, engine='c', usecols=[0,1,2,11,17])
artists.columns = ['artist_id','artist_mbid','artist_name','start_area1', 'start_area2']
artists.head()

artist_id                           artist_mbid      artist_name  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  
0          NaN          NaN  
1          NaN          NaN  
2          NaN          NaN  
3        222.0       7707.0  
4          NaN          NaN

In [133]:
#Let's see how many artists we have:
artists['artist_id'].nunique()

1476425

In [134]:
#How much info we have for each artist?
artists.isnull().sum(axis=0)

artist_id            0
artist_mbid          0
artist_name          8
start_area1     808442
start_area2    1274001
dtype: int64

What are the "start_area1" and "start_area2"? If we look at Musicbrainz's field description for each artist (https://musicbrainz.org/doc/Artist), we can see that:

Area: The artist area, as the name suggests, indicates the area with which an artist is primarily identified with. It is often, but not always, its birth/formation country.

We will keep this information as the artist's origin for later.

We need to incorporate as well the table called "artist credit", which gives us the artist credit_id. We will use this field to join later on each release with its artist:

In [135]:
artists_credit= pd.read_csv('Musicbrainz/Tables_used/artist_credit_name.txt',sep='\t', header=None, engine='c', usecols=[0,2,3])
artists_credit.columns = ['credit_id','artist_id','artist_name']
artists_credit.head()

credit_id  artist_id             artist_name
0     578352     578352           Gustav Ruppke
1     273232     273232                 Zachary
2     153193     153193  The High Level Ranters
3      32262      32262        Georges Brassens
4    1389968    1171184    Harvard of the South

In [136]:
#Let's join the artists with their credit id and verify that the matching is good:
df = pd.merge(artists, artists_credit, how='left', on='artist_id')
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id    artist_name_y  
0          NaN          NaN   822846.0            WIK▲N  
1          NaN          NaN        NaN              NaN  
2          NaN          NaN   273232.0          Zachary  
3        222.0       7707.0   101060.0  The Silhouettes  
4          NaN          NaN   145773.0     Aric Leavitt

In [137]:
#It looks like it makes sense. Please note that the credit id is sometimes equal to the artist_id, but not always:
df['check'] = df['artist_id'] - df['credit_id']
df['check'].nunique()

1270628

In [138]:
df.isnull().sum(axis=0)

artist_id              0
artist_mbid            0
artist_name_x         15
start_area1      1120376
start_area2      2109027
credit_id         461241
artist_name_y     461253
check             461241
dtype: int64

In [139]:
#We can now get rid of check and the duplicate artist_name column:
df.drop(labels=['check','artist_name_y'], axis=1, inplace=True)
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id  
0          NaN          NaN   822846.0  
1          NaN          NaN        NaN  
2          NaN          NaN   273232.0  
3        222.0       7707.0   101060.0  
4          NaN          NaN   145773.0

## <font color=blue>2) Release information</font>

### Data from Musicbrainz.org

The objective of this project is to visualize when each artist released for the first time a certain CD/Album/Single etc.

If we look at the "releases" table:

In [140]:
releases = pd.read_csv('Musicbrainz/Tables_used/release.txt',sep='\t', header=None, engine='c', usecols=[0,2,3,4])
releases.columns = ['release_id','release_group','credit_id','group_id']
releases.head()

release_id           release_group  credit_id  group_id
0           9       A Sorta Fairytale         60    896742
1          10       A Sorta Fairytale         60    896742
2          11       Glory of the 80's         60     95360
3          12  Silent All These Years         60    104189
4          26                  Demons      20211     94299

We can see, in the first 2 rows, that the same CD/Album can be released/remastered many times. According to Musicbrainz's field description for each release (https://musicbrainz.org/doc/Release):

"A MusicBrainz release represents the unique release (i.e. issuing) of a product on a specific date with specific release information such as the country, label, barcode and packaging. If you walk into a store and purchase an album or single, they are each represented in MusicBrainz as one release".

If we look at another release-related field in Musicbrainz, we find the "release group" (https://musicbrainz.org/doc/Release_Group):

"A release group, just as the name suggests, is used to group several different releases into a single logical entity. Every release belongs to one, and only one release group.

Both release groups and releases are "albums" in a general sense, but with an important difference: a release is something you can buy as media such as a CD or a vinyl record, while a release group embraces the overall concept of an album -- it doesn't matter how many CDs or editions/versions it had."

By reading these descriptions, we can clearly see that the release group is the table we are looking for as it represents a single creation, no matter how many times it has been edited or released afterwards. So we will have to keep the first release id for each release group.

In [141]:
release_country = pd.read_csv('Musicbrainz/Tables_used/release_country.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
release_country.columns = ['release_id','release_country','release_year']
release_country.head()

release_id  release_country  release_year
0           3               81        1997.0
1     1427792              107        2014.0
2           9               81        2002.0
3          10              221        2002.0
4          11               81        1999.0

In [142]:
df2 = pd.merge(releases, release_country, how='left', on='release_id')
df2.head()

release_id           release_group  credit_id  group_id  release_country  \
0           9       A Sorta Fairytale         60    896742             81.0   
1          10       A Sorta Fairytale         60    896742            221.0   
2          11       Glory of the 80's         60     95360             81.0   
3          12  Silent All These Years         60    104189             81.0   
4          26                  Demons      20211     94299            107.0   

   release_year  
0        2002.0  
1        2002.0  
2        1999.0  
3        1997.0  
4        1998.0

In [143]:
#Let's see how many releases we have:
df2['release_id'].nunique()

2198457

In [144]:
df2.isnull().sum(axis=0)

release_id              0
release_group           7
credit_id               0
group_id                0
release_country    287376
release_year       341983
dtype: int64

In [145]:
#We want to keep only the releases which have a release year, so we can drop the others:
df2.dropna(subset=['release_year'], axis=0, inplace=True)
df2['release_year'] = df2.release_year.astype(int,inplace=True)
df2['release_id'].nunique()

1859982

In [146]:
#Let's analyze the year column:
pd.options.display.max_rows = 2000
df2.groupby('release_year').count()

release_id  release_group  credit_id  group_id  release_country
release_year                                                                 
1                      2              2          2         2                2
4                      1              1          1         1                1
5                      5              5          5         5                5
7                      1              1          1         1                1
8                      2              2          2         2                2
10                     3              3          3         3                3
14                     1              1          1         1                1
17                     4              4          4         4                4
18                     1              1          1         1                1
19                     3              3          3         3                3
20                     2              2          2         2                2
21                     1              1          1         1                1
23                     1              1          1         1                1
24                     1              1          1         1                1
25                     2              2          2         2                2
28                     2              2          2         2                2
29                     2              2          2         2                2
31                     2              2          2         2                2
73                     1              1          1         1                1
195                    1              1          1         1                1
198                    1              1          1         1                1
199                    2              2          2         2                2
200                    4              4          4         4                4
201                    4              4          4         4                4
209                    2              2          2         2                2
666                    1              1          1         1                1
701                    1              1          1         1                1
996                    1              1          1         1                1
1009                   1              1          1         1                1
1029                   1              1          1         1                1
1198                   1              1          1         1                1
1694                   1              1          1         1                1
1886                   1              1          1         1                1
1889                   1              1          1         1                1
1890                 249            249        249       249              249
1891                  11             11         11        11               11
1892                 130            130        130       130              130
1893                 183            183        183       183              183
1894                  29             29         29        29               29
1895                   2              2          2         2                2
1896                   6              6          6         6                6
1897                  65             65         65        65               65
1898                 183            183        183       183              183
1899                 281            281        281       281              281
1900                 131            131        131       131              131
1901                 199            199        199       199              199
1902                 234            234        234       234              234
1903                 196            196        196       196              196
1904                 155            155        155       155              155
1905                 163            

By looking at the different year values, and, in order to have enough values per year, we could drop the rows whose year is below 1890 and above 2019. Our visualization would have 130 years, which is pretty good.

In [147]:
df2.drop(df2[df2['release_year'] < 1890].index , inplace=True)
df2.drop(df2[df2['release_year'] >2019].index , inplace=True)
df2.sort_values(by=['release_year']).head()

release_id                  release_group  credit_id  group_id  \
1266766      386919      Visions of Paradise Waltz      97546    712605   
1266956      386830  German Ballad with Variations      97546    712514   
1266958      386829  German Ballad with Variations      97546    712514   
1266960      386828           Mountain Bells Polka      97546    712513   
1266961      386827           Mountain Bells Polka      97546    712513   

         release_country  release_year  
1266766            222.0          1890  
1266956            222.0          1890  
1266958            222.0          1890  
1266960            222.0          1890  
1266961            222.0          1890

In [148]:
#Converting the year column to datetime for later:
df2['release_year'] = pd.to_datetime(df2['release_year'].astype(str), format='%Y')
df2.dtypes

release_id                  int64
release_group              object
credit_id                   int64
group_id                    int64
release_country           float64
release_year       datetime64[ns]
dtype: object

In [149]:
#We sort by release id and year (we could have 2 release groups with the same name but produced by different artists):
df2.sort_values(['release_group','release_year','credit_id'], ascending=[True,True,True], inplace=True)
df2.head()

release_id            release_group  credit_id  group_id  \
2026273     2163750                             2205562   1962329   
1648516     1846605                             1503027   1713833   
1250325     1714060    Beaux Soirs De Paris     1324142   1609358   
2116340     2265346                    Le 1     2291833   2042812   
1748061     1895266   M2Music HitDisc Vol. 1          1   1751021   

         release_country release_year  
2026273            240.0   2014-01-01  
1648516            240.0   2015-01-01  
1250325             73.0   1995-01-01  
2116340            240.0   2018-01-01  
1748061            222.0   2006-01-01

In [150]:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id  release_country  \
1836724     2378622    Artaxerxes    2392005   2132682            240.0   
1910376     2379252    Artaxerxes    2392005   2132682            221.0   
1909444     2379244    Artaxerxes    2392011   2133192            222.0   

        release_year  
1836724   1996-01-01  
1910376   2009-01-01  
1909444   2011-01-01

In [151]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df2.drop_duplicates(subset=['release_group','credit_id'],keep='first', inplace=True)
df2['release_id'].nunique()

1499614

In [152]:
#Just to double-check:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  group_id  release_country  \
1836724     2378622    Artaxerxes    2392005   2132682            240.0   
1909444     2379244    Artaxerxes    2392011   2133192            222.0   

        release_year  
1836724   1996-01-01  
1909444   2011-01-01

## <font color=blue>3) Matching releases with artists</font>

Now that we have both artist and releases dataframes, we can join them:

In [153]:
df3 = pd.merge(df2, df, how='left', on='credit_id')
df3.head()

release_id            release_group  credit_id  group_id  release_country  \
0     2163750                             2205562   1962329            240.0   
1     1846605                             1503027   1713833            240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358             73.0   
3     2265346                    Le 1     2291833   2042812            240.0   
4     1895266   M2Music HitDisc Vol. 1          1   1751021            222.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2018-01-01  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755   
4   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   

     artist_name_x  start_area1  start_area2  
0         Soul Glo       7707.0          NaN  
1      Ben Bennett          NaN          NaN  
2  Soixante Étages          NaN          NaN  
3         TedeuzeM      68613.0          NaN  
4  Various Artists          NaN          NaN

In [154]:
df3.isnull().sum(axis=0)

release_id              0
release_group           4
credit_id               0
group_id                0
release_country         0
release_year            0
artist_id             151
artist_mbid           151
artist_name_x         155
start_area1        430452
start_area2        959581
dtype: int64

In [155]:
df3['release_id'].nunique()

1499614

In [156]:
len(df3)

1724524

In [157]:
df3[df3['release_group']=='Artaxerxes']

release_id release_group  credit_id  group_id  release_country  \
119493     2378622    Artaxerxes    2392005   2132682            240.0   
119494     2378622    Artaxerxes    2392005   2132682            240.0   
119495     2378622    Artaxerxes    2392005   2132682            240.0   
119496     2378622    Artaxerxes    2392005   2132682            240.0   
119497     2378622    Artaxerxes    2392005   2132682            240.0   
119498     2378622    Artaxerxes    2392005   2132682            240.0   
119499     2378622    Artaxerxes    2392005   2132682            240.0   
119500     2378622    Artaxerxes    2392005   2132682            240.0   
119501     2378622    Artaxerxes    2392005   2132682            240.0   
119502     2379244    Artaxerxes    2392011   2133192            222.0   
119503     2379244    Artaxerxes    2392011   2133192            222.0   
119504     2379244    Artaxerxes    2392011   2133192            222.0   

       release_year  artist_id                           artist_mbid  \
119493   1996-01-01   391603.0  e3062782-ab7b-41bc-8e65-aeea16dc1a89   
119494   1996-01-01   124232.0  4e7f1926-8704-4545-a1a1-ded91651c884   
119495   1996-01-01   688791.0  f34e9da4-2ee7-4f27-aa34-adc5db791bec   
119496   1996-01-01  1129787.0  c33f733e-2bf4-402b-9455-1a293601a1cd   
119497   1996-01-01  1104538.0  5680c729-615b-47e2-969e-27a087c572fb   
119498   1996-01-01   402986.0  70af5d9a-c6e0-4fcf-9cde-4d3d00e0fcb0   
119499   1996-01-01   183632.0  954d1c83-259f-4a25-8878-10c19bb097af   
119500   1996-01-01    87510.0  857588a5-b7aa-4f72-a87b-8f03dca60e30   
119501   1996-01-01  1078968.0  93da7aaa-250b-46e1-b5ef-0ad78d46dc3f   
119502   2011-01-01   854064.0  a87f2b39-84c7-4888-935c-d41943bd7971   
119503   2011-01-01   124232.0  4e7f1926-8704-4545-a1a1-ded91651c884   
119504   2011-01-01   989288.0  4c05f6e6-7a40-437e-9f12-a90c1da7b4f8   

                    artist_name_x  start_area1  start_area2  
119493              Ian Partridge        221.0       1178.0  
119494                Thomas Arne        221.0       1178.0  
119495         Christopher Robson          NaN          NaN  
119496            Patricia Spence          NaN          NaN  
119497              Philippa Hyde        221.0          NaN  
119498  The Parley of Instruments        221.0       1178.0  
119499             Catherine Bott        221.0          NaN  
119500                Roy Goodman        221.0      30926.0  
119501       Richard Edgar‐Wilson          NaN          NaN  
119502    Classical Opera Company        221.0          NaN  
119503                Thomas Arne        221.0       1178.0  
119504                   Ian Page        221.0          NaN

If we look at the above, we can see that there is one line per each artist that participated for each release ID.

As we don't want to show duplicate releases, we need to keep only one artist per release. We will keep the first artist appearing for each release (even though we know this is not 100% accurate, but we have to avoid duplicates). This will afftect 224.910 rows under a total of 1.499.614 unique releases, so 14% of our dataset.

In [158]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df3.drop_duplicates(subset=['release_id'],keep='first', inplace=True)
df3['release_id'].nunique()

1499614

In [159]:
len(df3)

1499614

## <font color=blue>4) Geographical data</font>

### Data from Musicbrainz.org

The idea of the visualization is to see where each gender comes from, so, ideally, we would have to look at the artists origins (start area: last 2 columns of our dataframe).

In our dataframe df3, the 5th column "area_id" is related to the area where the release was produced. This isn't directly related to the origin of an artist/band, as many artists have to record their works in different countries/or areas.

Let's see for how many releases we have that information:

In [160]:
df3.isnull().sum(axis=0)

release_id              0
release_group           4
credit_id               0
group_id                0
release_country         0
release_year            0
artist_id             151
artist_mbid           151
artist_name_x         155
start_area1        404503
start_area2        876562
dtype: int64

In Musicbrainz's database, we have some tables related to the areas. Let's see how we can use them to input more geographical information into our dataframe:

In [161]:
areas = pd.read_csv('Musicbrainz/Tables_used/area.txt',sep='\t', header=None, engine='python', usecols=[0,2,3])
areas.columns = ['area_id','area_name','code_type']
areas.head()

area_id area_name  code_type
0    15449   Greccio        4.0
1       38    Canada        1.0
2       43     Chile        1.0
3       44     China        1.0
4       36  Cambodia        1.0

In [162]:
#Let's see the area types we have:
area_types = pd.read_csv('Musicbrainz/Tables_used/area_type.txt',sep='\t', header=None, engine='python', usecols=[1,3,4], error_bad_lines=False)
area_types.columns = ['type','code_type','definition']
area_types.head(20)

type  code_type                                         definition
0       Country          1  Country is used for areas included (or previou...
1   Subdivision          2  Subdivision is used for the main administrativ...
2        County          7  County is used for smaller administrative divi...
3  Municipality          4  Municipality is used for small administrative ...
4          City          3  City is used for settlements of any size, incl...
5      District          5  District is used for a division of a large cit...
6        Island          6  Island is used for islands and atolls which do...

ISO tables: In order to retrieve the ISO code for the countries and states, Musicbrainz provides us with 2 tables which contain: area_id and their ISO code (for area code_types 1 and 2: country and subdivision). These are international standard codes set by the International organization for Standardization (www.iso.org).

We will add this information to our areas dataframe, as this will be usefull for our visualization.

In [163]:
#First, we load the first ISO file:
ISO1 = pd.read_csv('Musicbrainz/Tables_used/iso_3166_1.txt',sep='\t', header=None, engine='python')
ISO1.columns = ['area_id','ISO_country']
ISO1['ISO_code'] = ISO1['ISO_country']

In [164]:
#Loading ISO2 file:
ISO2 = pd.read_csv('Musicbrainz/Tables_used/iso_3166_2.txt',sep=',', header=None, engine='python')
ISO2.columns = ['area_id','ISO_code', 'ISO_country']

In [165]:
#Now, we can add both ISO dataframes together:
ISO_codes = pd.concat([ISO1, ISO2])
ISO_codes.head()

ISO_code ISO_country  area_id
0       AF          AF        1
1       AL          AL        2
2       DZ          DZ        3
3       AS          AS        4
4       AD          AD        5

In [166]:
#And finally, we can merge the ISO codes into the areas dataframe:
areas_ISO = pd.merge(areas, ISO_codes, how='left', on='area_id')
areas_ISO.head()

area_id area_name  code_type ISO_code ISO_country
0    15449   Greccio        4.0      NaN         NaN
1       38    Canada        1.0       CA          CA
2       43     Chile        1.0       CL          CL
3       44     China        1.0       CN          CN
4       36  Cambodia        1.0       KH          KH

As Musicbrainz respects de historical information for each event, we can see that some countries that no longer exist do however appear in their list, for instance:

In [167]:
areas_ISO[areas_ISO['area_name'] == 'Soviet Union']

area_id     area_name  code_type ISO_code ISO_country
252      243  Soviet Union        1.0       SU          SU

In [168]:
areas_ISO[areas_ISO['area_name'] == 'Yugoslavia']

area_id   area_name  code_type ISO_code ISO_country
262      235  Yugoslavia        1.0       YU          YU

We'll update our areas_ISO dataframe by doing the following replacements:

- Czechoslovakia will become Czech Republic, country code CZ
- East Germany will become Germany, country code DE
- Soviet Union will become Russia, country code RU
- Serbia and Montenegro AND Yugoslavia will become Serbia, country code RS

In [169]:
areas_ISO.loc[7185] = 245, 'Czech Republic', 1, 'CZ', 'CZ'
areas_ISO.loc[5648] = 244, 'Germany', 1, 'DE', 'DE'
areas_ISO.loc[252] = 243, 'Russia', 1, 'RU', 'RU'
areas_ISO.loc[253] = 242, 'Serbia', 1, 'RS', 'RS'
areas_ISO.loc[262] = 235, 'Serbia', 1, 'RS', 'RS'

### Data from simplemaps.com

In our areas_ISO file we have detailed information about all the areas under categories 1 and 2 (countries and subdivisions). However, for areas whose type is 3 or above, we don't really have any detail abour which country and subdivision they belong to.

There is a free downloadable file in https://simplemaps.com/data/world-cities, which provides us with the names of the major cities in the world, as well as their country, coordinates and ISO code (for the country).

I have downloaded the csv version and we'll use it to enrich our areas columns.

In [170]:
cities = pd.read_csv('worldcities.csv', sep=',', usecols=[1,2,3,4,5], encoding='utf-8')
cities.columns = ['area_name','lat', 'long','country', 'country_ISO']
cities.head()

area_name      lat     long               country country_ISO
0             'Ataq  14.5500  46.8000                 Yemen          YE
1  's-Hertogenbosch  51.6833   5.3167           Netherlands          NL
2            `Ajlun  32.3333  35.7528                Jordan          JO
3            `Ajman  25.4056  55.4618  United Arab Emirates          AE
4            `Amran  15.6594  43.9439                 Yemen          YE

As we can see above, for each city we have its coordinates so, in order to retrieve also the region/subdivision, we could use the reverse_geocoder tool:

In [171]:
#We first create a new column called "coords" in which we'll gather both latitude and longitude:
cities['coords'] = list(zip(cities.lat, cities.long))
coords = tuple(cities['coords'].values.tolist())
#And now we use the reverse_geocoder utility to retrieve info for each pair of coordinates:
address = reverse_geocoder.search(coords)
cities['address'] = address
cities.head()

area_name      lat     long               country country_ISO  \
0             'Ataq  14.5500  46.8000                 Yemen          YE   
1  's-Hertogenbosch  51.6833   5.3167           Netherlands          NL   
2            `Ajlun  32.3333  35.7528                Jordan          JO   
3            `Ajman  25.4056  55.4618  United Arab Emirates          AE   
4            `Amran  15.6594  43.9439                 Yemen          YE   

               coords                                            address  
0       (14.55, 46.8)  {'lat': '14.53767', 'lon': '46.83187', 'name':...  
1   (51.6833, 5.3167)  {'lat': '51.69917', 'lon': '5.30417', 'name': ...  
2  (32.3333, 35.7528)  {'lat': '32.33326', 'lon': '35.75279', 'name':...  
3  (25.4056, 55.4618)  {'lat': '25.41111', 'lon': '55.43504', 'name':...  
4  (15.6594, 43.9439)  {'lat': '15.6594', 'lon': '43.94385', 'name': ...

In [172]:
#Let's see how is this new infor formatted:
cities['address'][0]

OrderedDict([('lat', '14.53767'),
             ('lon', '46.83187'),
             ('name', 'Ataq'),
             ('admin1', 'Shabwah'),
             ('admin2', 'Ataq'),
             ('cc', 'YE')])

In [173]:
#What about another row?
cities['address'][8564]

OrderedDict([('lat', '29.39005'),
             ('lon', '76.96949'),
             ('name', 'Panipat'),
             ('admin1', 'Haryana'),
             ('admin2', 'Panipat'),
             ('cc', 'IN')])

It looks like we would need the field "admin1" to retrieve the subdivision.

In [174]:
#We create an empty column:

cities['state'] = np.nan

#And fill it with the info we need:

for i in tqdm.tqdm(range(len(cities))):
    address = list(cities['address'][i].items())
    cities['state'][i] = address[3][1]


#We check the result:
cities.head()

100%|██████████| 12893/12893 [17:27<00:00, 12.36it/s]


area_name      lat     long               country country_ISO  \
0             'Ataq  14.5500  46.8000                 Yemen          YE   
1  's-Hertogenbosch  51.6833   5.3167           Netherlands          NL   
2            `Ajlun  32.3333  35.7528                Jordan          JO   
3            `Ajman  25.4056  55.4618  United Arab Emirates          AE   
4            `Amran  15.6594  43.9439                 Yemen          YE   

               coords                                            address  \
0       (14.55, 46.8)  {'lat': '14.53767', 'lon': '46.83187', 'name':...   
1   (51.6833, 5.3167)  {'lat': '51.69917', 'lon': '5.30417', 'name': ...   
2  (32.3333, 35.7528)  {'lat': '32.33326', 'lon': '35.75279', 'name':...   
3  (25.4056, 55.4618)  {'lat': '25.41111', 'lon': '55.43504', 'name':...   
4  (15.6594, 43.9439)  {'lat': '15.6594', 'lon': '43.94385', 'name': ...   

           state  
0        Shabwah  
1  North Brabant  
2          Ajlun  
3          Ajman  
4          Omran

In [175]:
#We can get rid of the columns we don't need:
cities.drop(labels=['lat', 'long', 'coords','address'], axis=1, inplace=True)

Note: as we will merge the above dataframe with areas_ISO using the "area_name" as key, we need to make sure that we remove the areas which have the same name, as we don't want to input the wrong information (2 cities from different countries or subdivisions can have the same name):

In [176]:
#We drop all the duplicate rows for area_name (to avoid confusion):
cities.drop_duplicates(subset='area_name', keep=False, inplace=True)

Now, we need to follow the same porocedure with the file areas_ISO, but in this case we'll focus only in the rows which don't have any info in the field "country_ISO" (as this is what we want to identify)

In [177]:
#We create the dataframe that we need to focus on:
to_match = areas_ISO[areas_ISO['ISO_country'].isnull()]
#We delete the duplicated area_names to avoid mismatching:
to_match.drop_duplicates(subset='area_name', keep=False, inplace=True)

In [178]:
#We merge to_match and cities:
matched = pd.merge(to_match, cities, how='left', on='area_name')
matched.head()

area_id                  area_name  code_type ISO_code ISO_country country  \
0    15449                    Greccio        4.0      NaN         NaN     NaN   
1     9014                      Pu'er        3.0      NaN         NaN     NaN   
2     8558                       Hill        3.0      NaN         NaN     NaN   
3    13703  Montecatini Val di Cecina        4.0      NaN         NaN     NaN   
4    14309          Casale Monferrato        4.0      NaN         NaN     NaN   

  country_ISO state  
0         NaN   NaN  
1         NaN   NaN  
2         NaN   NaN  
3         NaN   NaN  
4         NaN   NaN

In [179]:
matched[matched['state'].notnull()]

area_id                   area_name  code_type ISO_code ISO_country  \
7       115503                      Mardin        3.0      NaN         NaN   
24       88335                  Cienfuegos        3.0      NaN         NaN   
29      115508                   Satu Mare        3.0      NaN         NaN   
50        5057                   Ljubljana        3.0      NaN         NaN   
55       95867                 Cluj-Napoca        3.0      NaN         NaN   
58        5058                    Katowice        3.0      NaN         NaN   
85       88340                      Goyang        3.0      NaN         NaN   
102      91116             Hoffman Estates        3.0      NaN         NaN   
106       5242                   The Hague        3.0      NaN         NaN   
120       5243                       Porto        3.0      NaN         NaN   
148       5245                    Mariupol        3.0      NaN         NaN   
158       5246                 Tallahassee        3.0      NaN         NaN   
163       5063                     Vrhnika        3.0      NaN         NaN   
168       5703                    Poquoson        3.0      NaN         NaN   
175       5064                     Plovdiv        3.0      NaN         NaN   
192      98749                  Los Mochis        3.0      NaN         NaN   
193       5065                    Istanbul        3.0      NaN         NaN   
205       5066                      Zwolle        3.0      NaN         NaN   
214     115518                   Glen Rock        3.0      NaN         NaN   
231      13723                        Susa        4.0      NaN         NaN   
253     117943                    Mandurah        3.0      NaN         NaN   
277       5251                       Boise        3.0      NaN         NaN   
298       5072                      Gdynia        3.0      NaN         NaN   
305       5073                      Modena        3.0      NaN         NaN   
308       5252                      Lublin        3.0      NaN         NaN   
368     115523                New Liskeard        3.0      NaN         NaN   
389       5077                    Szczecin        3.0      NaN         NaN   
407       5078                        Nuuk        3.0      NaN         NaN   
429       5221                     Chengdu        3.0      NaN         NaN   
473       5082                 Novosibirsk        3.0      NaN         NaN   
491       5084                       Dubai        3.0      NaN         NaN   
492       5256                Invercargill        3.0      NaN         NaN   
493       5112                 Cherepovets        3.0      NaN         NaN   
496       5085                       Celje        3.0      NaN         NaN   
514       6497                   Claremore        3.0      NaN         NaN   
516       5397                       Hamar        3.0      NaN         NaN   
518       5257                       Karaj        3.0      NaN         NaN   
527       5086                   Volgograd        3.0      NaN         NaN   
528       5111                     Tallinn        3.0      NaN         NaN   
534       6395                   Tonawanda        3.0      NaN         NaN   
535       7848               Hermosa Beach        3.0      NaN         NaN   
543       6108                       Pasco        3.0      NaN         NaN   
544       6346             Port Washington        3.0      NaN         NaN   
553       8955                    Shangrao        3.0      NaN         NaN   
557       5562                        Saga        3.0      NaN         NaN   
565       8379                   Yeniseysk        3.0      NaN         NaN   
573       5258                Johannesburg        3.0      NaN         NaN   
581       7851                     Livonia        3.0      NaN         NaN   
584       9551                   Urbandale        3.0      NaN         NaN   
587       6223                      Elmira        3.0      NaN         NaN   
588       6278               

What we want now is to retrieve also the subdivision for the rows we just identified now. For that, we'll create a specific dataframe, coming from areas_ISO where the code type is equal to 2:

In [180]:
subdivisions = areas_ISO[areas_ISO['code_type'] == 2]
subdivisions.head()

area_id  area_name  code_type ISO_code ISO_country
26      1949  Borovnica        2.0     SI-5          SI
76      1969  Dravograd        2.0    SI-25          SI
118     2205  Agio Oros        2.0    GR-69          GR
171     4695       Roma        2.0    IT-RM          IT
192     1950      Bovec        2.0     SI-6          SI

In [181]:
#We create an extra column containing area_name + ISO_country to match later:
subdivisions['ISO_match'] = subdivisions['area_name'] + subdivisions['ISO_country']
subdivisions.head()

area_id  area_name  code_type ISO_code ISO_country    ISO_match
26      1949  Borovnica        2.0     SI-5          SI  BorovnicaSI
76      1969  Dravograd        2.0    SI-25          SI  DravogradSI
118     2205  Agio Oros        2.0    GR-69          GR  Agio OrosGR
171     4695       Roma        2.0    IT-RM          IT       RomaIT
192     1950      Bovec        2.0     SI-6          SI      BovecSI

In [182]:
#We do the same in our matched dataframe:
matched['ISO_match'] = matched['state'] + matched['country_ISO']
#We remove the rows which don't have an ISO_match:
matched.dropna(subset=['ISO_match'], axis=0, inplace=True)

In [183]:
#We merge matched with this subdivisions dataframe to add the subdivision ISO-code into it:
areas_3 = pd.merge(matched, subdivisions[['ISO_code','ISO_match']], how='left', on='ISO_match')
areas_3.head()

area_id    area_name  code_type ISO_code_x ISO_country   country  \
0   115503       Mardin        3.0        NaN         NaN    Turkey   
1    88335   Cienfuegos        3.0        NaN         NaN      Cuba   
2   115508    Satu Mare        3.0        NaN         NaN   Romania   
3     5057    Ljubljana        3.0        NaN         NaN  Slovenia   
4    95867  Cluj-Napoca        3.0        NaN         NaN   Romania   

  country_ISO       state     ISO_match ISO_code_y  
0          TR      Mardin      MardinTR      TR-47  
1          CU  Cienfuegos  CienfuegosCU       CU-6  
2          RO   Satu Mare   Satu MareRO      RO-SM  
3          SI   Ljubljana   LjubljanaSI      SI-61  
4          RO        Cluj        ClujRO      RO-CJ

Now, we can merge areas_ISO with areas_3:

In [184]:
areas_ISO1 = pd.merge(areas_ISO, areas_3[['area_id','ISO_code_y', 'country_ISO']], how='left', on='area_id')
areas_ISO1.head()

area_id area_name  code_type ISO_code ISO_country ISO_code_y country_ISO
0    15449   Greccio        4.0      NaN         NaN        NaN         NaN
1       38    Canada        1.0       CA          CA        NaN         NaN
2       43     Chile        1.0       CL          CL        NaN         NaN
3       44     China        1.0       CN          CN        NaN         NaN
4       36  Cambodia        1.0       KH          KH        NaN         NaN

In [185]:
areas_ISO1[areas_ISO1['code_type'] >2]

area_id                                          area_name  code_type  \
0         15449                                            Greccio        4.0   
42         9014                                              Pu'er        3.0   
67         8195                                            Milford        3.0   
68         8558                                               Hill        3.0   
70        13703                          Montecatini Val di Cecina        4.0   
71        14309                                  Casale Monferrato        4.0   
72        14324                                    Palazzo Pignano        4.0   
73        14332                                        Maccastorna        4.0   
74       115503                                             Mardin        3.0   
75         8060                                             Maldon        3.0   
77         8187                                              Serik        3.0   
78         8375                                             Dobříš        3.0   
79         7571                                          Braunfels        3.0   
80        14883                                    Cerretto Langhe        4.0   
81        88334                                           Descanso        3.0   
83        15450                                           Configni        4.0   
110      115504                                             Edison        3.0   
131      117941                                           Bahçecik        3.0   
147      115505                                             Darwin        3.0   
158       13704                                             Palaia        4.0   
159       14310                                        Graffignano        4.0   
160       14315                                            Celleno        4.0   
161       95863                                         Chautauqua        3.0   
162       14884                                            Cervere        4.0   
163       15451                                     Fara in Sabina        4.0   
166       98703                              Ciudad Nezahualcóyotl        3.0   
167      115506                                       Elcho Island        6.0   
170        8858                                          Huangshan        3.0   
172       88335                                         Cienfuegos        3.0   
173       16174                                             Andora        4.0   
225       13705                                          Scalenghe        4.0   
226       13811                                       Castelcovati        4.0   
234       13849                                            Gianico        4.0   
238      115508                                          Satu Mare        3.0   
248       13927                                  Montecchio Emilia        4.0   
267       88336                                          Burnt Oak        3.0   
268       13931                                          Guastalla        4.0   
274       95864                                     Brookmans Park        3.0   
276      115507                                         Galiwin'ku        3.0   
284       19647                                   Orsara di Puglia        4.0   
289       14311                                          Corchiano        4.0   
299      104951                                         Twin Hills        3.0   
324        5699                                              Dębno        3.0   
325        5056                                             Warsaw        3.0   
341       13706                                     Casciana Terme        4.0   
343       88337                                            Tequila        3.0   
344       95865                                       Sakhi Sarwar        3.0   
345       14312                                            Gradoli        4.0   
346       15452                        

Now, what we have to to is input the information contained in the last two columns into the 4th and 5th for the rows whose code type is above 2.

In [186]:
#For the rows whose code_type is greater than 2 (ie: cities), we input the country_ISO into ISO_code and ISO_country:
areas_ISO1.ISO_code = np.where(np.logical_and(areas_ISO1.code_type > 2, areas_ISO1.ISO_code_y.notnull()), areas_ISO1.ISO_code_y, areas_ISO1.ISO_code)
areas_ISO1.ISO_country = np.where(np.logical_and(areas_ISO1.code_type > 2, areas_ISO1.country_ISO.notnull()), areas_ISO1.country_ISO, areas_ISO1.ISO_country)

In [187]:
areas_ISO1.head()

area_id area_name  code_type ISO_code ISO_country ISO_code_y country_ISO
0    15449   Greccio        4.0      NaN         NaN        NaN         NaN
1       38    Canada        1.0       CA          CA        NaN         NaN
2       43     Chile        1.0       CL          CL        NaN         NaN
3       44     China        1.0       CN          CN        NaN         NaN
4       36  Cambodia        1.0       KH          KH        NaN         NaN

In [188]:
#We can now delete the two last columns as they are now the same as the 4th and 5th:
areas_ISO1.drop(labels=['ISO_code_y', 'country_ISO'], axis=1, inplace=True)
areas_ISO1.head()

area_id area_name  code_type ISO_code ISO_country
0    15449   Greccio        4.0      NaN         NaN
1       38    Canada        1.0       CA          CA
2       43     Chile        1.0       CL          CL
3       44     China        1.0       CN          CN
4       36  Cambodia        1.0       KH          KH

In order for our visualization to have the right amount of detail to see the geographical evolution of each genre, we need to select areas that have the same size and the same volume of releases. USA is by far the country that produces the most releases, so here is the level of detail we need:

- For the US: we will keep the state/subdivision as their origin area. 
- For the rest of the countries, we will keep their country as their origin area.

In both cases, we need to retrieve the coordinates.

In [189]:
#First, let's remove from the areas the ones that are vague (they won't help us in our visualization):
areas_ISO1.set_index("area_name", inplace=True)
labels = ['[at sea]', '[space]', '[Worldwide]', 'Europe']
areas_ISO1.drop(labels, axis=0, inplace=True)
areas_ISO1.reset_index(inplace=True)

#### 1)Retrieving coordinates for the countries

https://gist.github.com/tadast/8827699 --> countries_codes_and_coordinates.csv

Added manually: Kosovo (XK) and South Sudan (SS), they were missing.
Also: for the Russian óblast "Leningradskaya Oblast’", as it doesn't have a capital, I marked the most central city as the coordinate origin (Volkhov). Same happened with "Moskovskaya Oblast’", for which I selected Podolsk.

In [190]:
country_coords = pd.read_csv('countries_codes_and_coordinates.csv', usecols=[1,4,5], encoding='utf-8')
country_coords.rename(columns={'Alpha-2 code':'ISO_country','Latitude (average)':'lat','Longitude (average)':'long'}, inplace=True)
country_coords['ISO_country'] = country_coords['ISO_country'].str.strip()
country_coords.head()

ISO_country      lat   long
0          AF  33.0000   65.0
1          AL  41.0000   20.0
2          DZ  28.0000    3.0
3          AS -14.3333 -170.0
4          AD  42.5000    1.6

In [191]:
country_coords.dropna(subset=['ISO_country'], axis=0, inplace=True)

In [192]:
#Merge our areas_ISO1 dataframe with country coords:
country_coords1 = pd.merge(areas_ISO1, country_coords, how='left', on='ISO_country')
country_coords1.head()

area_name  area_id  code_type ISO_code ISO_country   lat   long
0   Greccio    15449        4.0      NaN         NaN   NaN    NaN
1    Canada       38        1.0       CA          CA  60.0  -95.0
2     Chile       43        1.0       CL          CL -30.0  -71.0
3     China       44        1.0       CN          CN  35.0  105.0
4  Cambodia       36        1.0       KH          KH  13.0  105.0

In [193]:
#Let's analyze a specific case:
country_coords1[country_coords1['area_id'] == 454]

area_name  area_id  code_type ISO_code ISO_country   lat  long
587   Bonaire      454        2.0    BQ-BO          BQ   NaN   NaN
588   Bonaire      454        2.0   NL-BQ1          NL  52.5  5.75

There can be duplicate area_id for the cases where there is more than one ISO-code 2 for each. If we look at Wikipedia definition of this region (https://en.wikipedia.org/wiki/Bonaire), we can see that they currently are part of the Netherlands. 

For those cases, we'll keep the country where they belong to (ie: where the coordinates have been retrieved):

In [194]:
#We sort by area_id and latitude:
country_coords1.sort_values(by=['area_id','lat'], ascending=[False,True], inplace=True )

In [195]:
#And we remove duplicate rows, keeping the first occurrence:
country_coords1.drop_duplicates(subset='area_id', keep='first', inplace=True)

As we said before, we want the country coordinates for the non-large countries only. So, from this dataframe, we want to keep the following rows:

- Code type = 1 and coordinates not null
- Code type >1 and country code not equal to a large country and coordinates not null

We'll split the dataframe into 2, save the above mentioned group in one ("retrieved"), and keep searching for the coordinates of the rest ("pending").

In [196]:
#Countries and their coordinates:
subset_1 = country_coords1[country_coords1.code_type == 1 & country_coords1.lat.notnull()]
subset_1.isnull().any()

area_name      False
area_id        False
code_type      False
ISO_code       False
ISO_country    False
lat            False
long           False
dtype: bool

In [197]:
#Subdivisions & cities and their country coordinates:
subset_2 = country_coords1[(country_coords1.code_type > 1) & (country_coords1.lat.notnull())]
subset_2.head()

area_name  area_id  code_type ISO_code ISO_country   lat   long
118439        Paramus   118558        3.0    US-NJ          US  38.0  -97.0
118426         Meknes   118545        3.0      NaN          MA  32.0   -5.0
118421      Arcoverde   118540        3.0    BR-PE          BR -10.0  -55.0
118417       Lillooet   118536        3.0    CA-BC          CA  60.0  -95.0
118379  Alice Springs   118506        3.0    AU-NT          AU -27.0  133.0

In [198]:
#Retrieve only the non large countries:
large = ['US']
subset_2_correct = subset_2[~subset_2['ISO_country'].isin(large)]
subset_2_correct.head()

area_name  area_id  code_type ISO_code ISO_country   lat   long
118426         Meknes   118545        3.0      NaN          MA  32.0   -5.0
118421      Arcoverde   118540        3.0    BR-PE          BR -10.0  -55.0
118417       Lillooet   118536        3.0    CA-BC          CA  60.0  -95.0
118379  Alice Springs   118506        3.0    AU-NT          AU -27.0  133.0
118367          Sikar   118494        3.0    IN-RJ          IN  20.0   77.0

In [199]:
#Keeping our final areas in one dataframe:
retrieved = pd.concat([subset_1, subset_2_correct], ignore_index=True)

In [200]:
#Now, we need to select the areas that are actually not contained in our "retrieved" dataframe:
retrieved_list = retrieved.area_id.values.tolist()
pending = country_coords1[~country_coords1['area_id'].isin(retrieved_list)]
pending.head()

area_name  area_id  code_type ISO_code ISO_country  lat  long
113618       Castleford   118577        3.0      NaN         NaN  NaN   NaN
113025  Guminokiyokocho   118576        5.0      NaN         NaN  NaN   NaN
112282          Linares   118575        3.0      NaN         NaN  NaN   NaN
111676        Greenford   118574        5.0      NaN         NaN  NaN   NaN
111590         Changshu   118573        3.0      NaN         NaN  NaN   NaN

In [201]:
#We can drop the columns lat & long for now:
pending.drop(labels=['lat', 'long'], axis=1, inplace=True)

#### 2)Retrieving coordinates for the subdivisions

In this case, in order to retrieve the coordinates for each large country subdivision, we can use the same file we used for generating our cities dataframe, remove all the unnecessary countries, and filter by the administrative capital of each subdivision. Those coordinates will represent the subdivision in our visualization.

In [202]:
all_countries = pd.read_csv('worldcities.csv', sep=',', usecols=[1,2,3,4,5,7,8], encoding='utf-8')
all_countries.columns = ['area_name','lat', 'long','country', 'country_ISO', 'subdivision', 'capital']
all_countries.head()

area_name      lat     long               country country_ISO  \
0             'Ataq  14.5500  46.8000                 Yemen          YE   
1  's-Hertogenbosch  51.6833   5.3167           Netherlands          NL   
2            `Ajlun  32.3333  35.7528                Jordan          JO   
3            `Ajman  25.4056  55.4618  United Arab Emirates          AE   
4            `Amran  15.6594  43.9439                 Yemen          YE   

     subdivision capital  
0        Shabwah   admin  
1  Noord-Brabant   admin  
2         ‘Ajlūn   admin  
3         ‘Ajmān   admin  
4         ‘Amrān   admin

In [203]:
#We keep only the US:
large_countries = all_countries[all_countries['country_ISO'].isin(large)]
large_countries.head()

area_name      lat      long        country country_ISO     subdivision  \
20  Abbeville  29.9751  -92.1265  United States          US       Louisiana   
21  Abbeville  34.1787  -82.3774  United States          US  South Carolina   
29   Aberdeen  46.9768 -123.8083  United States          US      Washington   
30   Aberdeen  35.1345  -79.4314  United States          US  North Carolina   
31   Aberdeen  39.5146  -76.1731  United States          US        Maryland   

   capital  
20     NaN  
21     NaN  
29     NaN  
30     NaN  
31     NaN

In [204]:
large_countries.country_ISO.value_counts()

US    4848
Name: country_ISO, dtype: int64

In [205]:
capitals = ['admin', 'primary']
large_countries_capitals = large_countries[large_countries['capital'].isin(capitals)]
large_countries_capitals.head()

area_name      lat     long        country country_ISO subdivision  \
204     Albany  42.6664 -73.7987  United States          US    New York   
412  Annapolis  38.9705 -76.5047  United States          US    Maryland   
641    Atlanta  33.7627 -84.4231  United States          US     Georgia   
672    Augusta  44.3341 -69.7319  United States          US       Maine   
682     Austin  30.3038 -97.7545  United States          US       Texas   

    capital  
204   admin  
412   admin  
641   admin  
672   admin  
682   admin

In [206]:
len(large_countries_capitals)

51

In [207]:
#Is there any duplicated area_name in this case?
large_countries_capitals.duplicated(subset='area_name').any()

False

As I didn't have any file containing the country_ISO, ISO_code for the region and the name of the Subdivision for the US, I searched in Wikipedia, and found it:

https://en.wikipedia.org/wiki/ISO_3166-2:US

I have manually copied it in the file: subdivision_names.csv.

By using this file we'll be able to join all the dataframes accordingly.

In [208]:
#Let's open the file:
subdivision_names = pd.read_csv('subdivision_names.csv', sep='\t', header=0, encoding='utf-8')
subdivision_names.head()

ISO_country ISO_code                   subdivision
0          AU   AU-ACT  Australian Capital Territory
1          AU   AU-NSW               New South Wales
2          AU    AU-NT            Northern Territory
3          AU   AU-QLD                    Queensland
4          AU    AU-SA               South Australia

In [209]:
#We can retrieve the capital's coordinates from large_countries_capitals:
subdivision_coords = pd.merge(subdivision_names, large_countries_capitals[['subdivision', 'lat', 'long']], how='left', on='subdivision')
subdivision_coords.head()

ISO_country ISO_code                   subdivision  lat  long
0          AU   AU-ACT  Australian Capital Territory  NaN   NaN
1          AU   AU-NSW               New South Wales  NaN   NaN
2          AU    AU-NT            Northern Territory  NaN   NaN
3          AU   AU-QLD                    Queensland  NaN   NaN
4          AU    AU-SA               South Australia  NaN   NaN

In [210]:
#Now we can match our pending areas with the subdivision coords dataframe using the ISO_code:
subset2 = pd.merge(pending, subdivision_coords[['ISO_code', 'subdivision', 'lat', 'long']], how='left', on='ISO_code')
subset2.head()

area_name  area_id  code_type ISO_code ISO_country subdivision  lat  \
0       Castleford   118577        3.0      NaN         NaN         NaN  NaN   
1  Guminokiyokocho   118576        5.0      NaN         NaN         NaN  NaN   
2          Linares   118575        3.0      NaN         NaN         NaN  NaN   
3        Greenford   118574        5.0      NaN         NaN         NaN  NaN   
4         Changshu   118573        3.0      NaN         NaN         NaN  NaN   

   long  
0   NaN  
1   NaN  
2   NaN  
3   NaN  
4   NaN

In [211]:
#We keep as retrieved 2 the rows for which we retrieved the coordinates:
retrieved2 = subset2[subset2['lat'].notnull()]
retrieved2.head()

area_name  area_id  code_type ISO_code ISO_country subdivision  \
19          Paramus   118558        3.0    US-NJ          US  New Jersey   
108    Midland Park   118464        3.0    US-NJ          US  New Jersey   
129      Horseheads   118443        3.0    US-NY          US    New York   
131  Palisades Park   118441        3.0    US-NJ          US  New Jersey   
149         Tenafly   118422        3.0    US-NJ          US  New Jersey   

         lat     long  
19   40.2237 -74.7640  
108  40.2237 -74.7640  
129  42.6664 -73.7987  
131  40.2237 -74.7640  
149  40.2237 -74.7640

In [212]:
retrieved2.isnull().sum(axis=0)

area_name      0
area_id        0
code_type      0
ISO_code       0
ISO_country    0
subdivision    0
lat            0
long           0
dtype: int64

In [219]:
#And we keep as pending the rest of the rows:
pending2 = subset2[subset2['lat'].isnull()]
pending2.head()

area_name  area_id  code_type ISO_code ISO_country subdivision  lat  \
0       Castleford   118577        3.0      NaN         NaN         NaN  NaN   
1  Guminokiyokocho   118576        5.0      NaN         NaN         NaN  NaN   
2          Linares   118575        3.0      NaN         NaN         NaN  NaN   
3        Greenford   118574        5.0      NaN         NaN         NaN  NaN   
4         Changshu   118573        3.0      NaN         NaN         NaN  NaN   

   long  
0   NaN  
1   NaN  
2   NaN  
3   NaN  
4   NaN

In [220]:
len(pending2)

108554

In [221]:
pending2.isnull().sum(axis=0)

area_name           0
area_id             0
code_type          20
ISO_code       108538
ISO_country    108541
subdivision    108554
lat            108554
long           108554
dtype: int64

In [232]:
#It looks like some rows do have an ISO country:
retrieved3 = pending2[pending2['ISO_country'].notnull()]
retrieved3.head()

area_name  area_id  code_type ISO_code ISO_country subdivision  lat  \
12402      Marigot   105933        3.0      NaN          MF         NaN  NaN   
12412     Gustavia   105916        3.0      NaN          BL         NaN  NaN   
95337   Willemstad    21724        3.0      NaN          CW         NaN  NaN   
103521      Nangan    12753        3.0      NaN          TW         NaN  NaN   
104155    Pingzhen    12079        3.0      NaN          TW         NaN  NaN   

        long  
12402    NaN  
12412    NaN  
95337    NaN  
103521   NaN  
104155   NaN

In [233]:
#What about the pending areas?
retrieved3.ISO_country.value_counts()

TW    8
XK    1
BQ    1
MF    1
CW    1
BL    1
Name: ISO_country, dtype: int64

In [234]:
retrieved3[retrieved3['ISO_country'] == 'TW']

area_name  area_id  code_type ISO_code ISO_country subdivision  lat  \
103521    Nangan    12753        3.0      NaN          TW         NaN  NaN   
104155  Pingzhen    12079        3.0      NaN          TW         NaN  NaN   
104162    Magong    12072        3.0      NaN          TW         NaN  NaN   
104163      Puzi    12071        3.0      NaN          TW         NaN  NaN   
104164    Taibao    12070        3.0      NaN          TW         NaN  NaN   
104169    Zhubei    12065        3.0      NaN          TW         NaN  NaN   
104170   Yangmei    12064        3.0      NaN          TW         NaN  NaN   
104172   Zhongli    12062        3.0      NaN          TW         NaN  NaN   

        long  
103521   NaN  
104155   NaN  
104162   NaN  
104163   NaN  
104164   NaN  
104169   NaN  
104170   NaN  
104172   NaN

It looks like the 8 TW rows all belong to Taiwan cities. As Taiwan is officially considered as part of the Republic of China, we can manually change all these rows:

In [235]:
retrieved3.ISO_country = np.where(retrieved3.ISO_country.isin(['TW']), 'CN', retrieved3.ISO_country)
retrieved3.subdivision = np.where(retrieved3.ISO_country.isin(['CN']), np.nan , retrieved3.subdivision)
retrieved3.lat = np.where(retrieved3.ISO_country.isin(['CN']), 35.0 , retrieved3.lat)
retrieved3.long = np.where(retrieved3.ISO_country.isin(['CN']), 105.0 , retrieved3.long)
retrieved3.ISO_country.value_counts()

CN    8
XK    1
MF    1
BQ    1
CW    1
BL    1
Name: ISO_country, dtype: int64

In [236]:
#What about the others?
retrieved3[retrieved3['ISO_country'] != 'CN']

area_name  area_id  code_type ISO_code  \
12402                            Marigot   105933        3.0      NaN   
12412                           Gustavia   105916        3.0      NaN   
95337                         Willemstad    21724        3.0      NaN   
110553                            Kosovo     2358        NaN       XK   
110607  Bonaire, Sint Eustatius and Saba      258        1.0       BQ   

       ISO_country subdivision  lat  long  
12402           MF         NaN  NaN   NaN  
12412           BL         NaN  NaN   NaN  
95337           CW         NaN  NaN   NaN  
110553          XK         NaN  NaN   NaN  
110607          BQ         NaN  NaN   NaN

As for the rest: 

- Marigot is part of the French territory, and so is Gustavia. We can change their info to the one from France.
- Willemstad is part of the Netherlands, and so is Bonaire we can change it too.
- Kosovo is a country and we have its coordinates so we can also change it.

In [237]:
retrieved3.set_index('area_id', drop=False, inplace=True)
retrieved3.loc[105933] = 'Marigot', 105933, 3.0, np.nan, 'FR', np.nan, 46.0, 2.0
retrieved3.loc[105916] = 'Gustavia', 105916, 3.0, np.nan, 'FR', np.nan, 46.0, 2.0
retrieved3.loc[21724] = 'Willemstad',21724, 3.0 , np.nan, 'NL', np.nan, 52.5, 5.75
retrieved3.loc[258] = 'Bonaire, Sint Eustatius and Saba', 258,  3.0 , np.nan,'NL', np.nan, 52.5, 5.75
retrieved3.loc[2358] = 'Kosovo', 2358, 1.0 , np.nan, 'XK', np.nan, 42.66, 21.17
retrieved3.reset_index(drop=True, inplace=True)

In [238]:
retrieved3.isnull().sum(axis=0)

area_name       0
area_id         0
code_type       0
ISO_code       13
ISO_country     0
subdivision    13
lat             0
long            0
dtype: int64

What about the areas we didn't identify?

In [240]:
pending3 = pending2[pending2['ISO_country'].isnull()]
pending3.head(1000)

area_name  area_id  code_type  \
0                                            Castleford   118577        3.0   
1                                       Guminokiyokocho   118576        5.0   
2                                               Linares   118575        3.0   
3                                             Greenford   118574        5.0   
4                                              Changshu   118573        3.0   
5                                            Litoměřice   118572        3.0   
6                                           Maglebrænde   118571        3.0   
7                                              Leordina   118570        3.0   
8                                              Kullamaa   118569        3.0   
9                                                Simuna   118568        3.0   
10                                           Pontefract   118567        3.0   
11                                       Oron-le-Châtel   118566        4.0   
12                                             Netolice   118565        3.0   
13                                              Crimora   118564        3.0   
14                                            Karlskoga   118563        3.0   
15                                            Wakefield   118562        5.0   
16                                             Tebworth   118561        3.0   
17                                          Sanderstead   118560        5.0   
18                                          Zevenbergen   118559        3.0   
20                                  Montgomery Township   118557        4.0   
21                                                  Lar   118556        3.0   
22                                            Gushikawa   118555        3.0   
23                                          Shimabukuro   118554        5.0   
24                                            Bandhagen   118553        5.0   
25                                               Weston   118552        5.0   
26                                                 York   118551        5.0   
27                                             Vineland   118550        5.0   
28                                                Βόλος   118549        3.0   
29                                              Sidbury   118548        3.0   
30                                             McDonald   118547        3.0   
31                                               Golden   118546        3.0   
32                                              Aliança   118544        4.0   
33                                               Jarvis   118543        3.0   
34                                              Leksand   118542        3.0   
35                                              Guarana   118541        3.0   
36                              Saint-Jacques-le-Mineur   118539        3.0   
37    Les Jardins-de-Napierville Regional County Mun...   118538        4.0   
38                                                 Bise   118537        5.0   
39                                         Streekermoor   118535        3.0   
40                                           Neusüdende   118534        3.0   
41                                              Northam   118533        3.0   
42                                              Copiapó   118532        3.0   
43                                            Fort Kent   118531        3.0   
44                                              Coeburn   118530        3.0   
45                                              McClure   118529        3.0   
46                                             Canarsie   118528        5.0   
47                                              Whitney   118527        3.0   
48                             Saint-Gabriel-de-Brandon   118526        4.0   
49                                             Lievegem   118525        4.0   
50                                              Kruisem   118524        4.0   
51               

In [241]:
len(pending3)

108541

In [247]:
pending3.code_type.value_counts()

3.0    70722
4.0    32321
7.0     3502
5.0     1260
2.0      611
6.0      104
1.0        2
Name: code_type, dtype: int64

In [248]:
pending3.isnull().sum(axis=0)

area_name           0
area_id             0
code_type          19
ISO_code       108527
ISO_country    108541
subdivision    108541
lat            108541
long           108541
dtype: int64

In [250]:
pending3[pending3['ISO_code'].notnull()]

area_name  area_id  code_type ISO_code ISO_country subdivision  \
18260   Kavango West    99994        2.0    NA-KW         NaN         NaN   
18261   Kavango East    99993        2.0    NA-KE         NaN         NaN   
110541     Ohangwena     3533        2.0    NA-OW         NaN         NaN   
110542      Oshikoto     3532        2.0    NA-OT         NaN         NaN   
110543       Omusati     3531        2.0    NA-OS         NaN         NaN   
110544        Oshana     3530        2.0    NA-ON         NaN         NaN   
110545       Omaheke     3528        2.0    NA-OH         NaN         NaN   
110546  Otjozondjupa     3527        2.0    NA-OD         NaN         NaN   
110547        Kunene     3526        2.0    NA-KU         NaN         NaN   
110548        Khomas     3525        2.0    NA-KH         NaN         NaN   
110549       ǀǀKaras     3524        2.0    NA-KA         NaN         NaN   
110550        Hardap     3523        2.0    NA-HA         NaN         NaN   
110551        Erongo     3522        2.0    NA-ER         NaN         NaN   
110552       Zambezi     3521        2.0    NA-CA         NaN         NaN   

        lat  long  
18260   NaN   NaN  
18261   NaN   NaN  
110541  NaN   NaN  
110542  NaN   NaN  
110543  NaN   NaN  
110544  NaN   NaN  
110545  NaN   NaN  
110546  NaN   NaN  
110547  NaN   NaN  
110548  NaN   NaN  
110549  NaN   NaN  
110550  NaN   NaN  
110551  NaN   NaN  
110552  NaN   NaN

It looks like the above Namibian subdivisions have been identified but neither their country or coordinates appear.

In [257]:
pending3[pending3['code_type'] == 1.0]

area_name  area_id  code_type ISO_code ISO_country  \
116     Kingdom of the Netherlands   118456        1.0      NaN         NaN   
110608                     Namibia      147        1.0      NaN         NaN   

       subdivision  lat  long  
116            NaN  NaN   NaN  
110608         NaN  NaN   NaN

The above areas haven't been identified either. We will manually fill in the values and keep the areas in retrieved4.

In [261]:
pending3.loc[116] = 'Netherlands', 118456,  1.0 , np.nan,'NL', np.nan, 52.5, 5.75
pending3.loc[110608] = 'Namibia', 147,  1.0 , np.nan,'NA', np.nan, -22.0, 17.0
pending3.ISO_country = np.where(pending3.ISO_code.notnull(), 'NA', pending3.ISO_country)
pending3.lat = np.where(pending3.ISO_code.notnull(), -22.0, pending3.lat)
pending3.long = np.where(pending3.ISO_code.notnull(), 17.0, pending3.long)

In [262]:
retrieved4 = pending3[pending3['ISO_country'].notnull()]
retrieved4

area_name  area_id  code_type ISO_code ISO_country subdivision  \
116      Netherlands   118456        1.0      NaN          NL         NaN   
18260   Kavango West    99994        2.0    NA-KW          NA         NaN   
18261   Kavango East    99993        2.0    NA-KE          NA         NaN   
110541     Ohangwena     3533        2.0    NA-OW          NA         NaN   
110542      Oshikoto     3532        2.0    NA-OT          NA         NaN   
110543       Omusati     3531        2.0    NA-OS          NA         NaN   
110544        Oshana     3530        2.0    NA-ON          NA         NaN   
110545       Omaheke     3528        2.0    NA-OH          NA         NaN   
110546  Otjozondjupa     3527        2.0    NA-OD          NA         NaN   
110547        Kunene     3526        2.0    NA-KU          NA         NaN   
110548        Khomas     3525        2.0    NA-KH          NA         NaN   
110549       ǀǀKaras     3524        2.0    NA-KA          NA         NaN   
110550        Hardap     3523        2.0    NA-HA          NA         NaN   
110551        Erongo     3522        2.0    NA-ER          NA         NaN   
110552       Zambezi     3521        2.0    NA-CA          NA         NaN   
110608       Namibia      147        1.0      NaN          NA         NaN   

         lat   long  
116     52.5   5.75  
18260  -22.0  17.00  
18261  -22.0  17.00  
110541 -22.0  17.00  
110542 -22.0  17.00  
110543 -22.0  17.00  
110544 -22.0  17.00  
110545 -22.0  17.00  
110546 -22.0  17.00  
110547 -22.0  17.00  
110548 -22.0  17.00  
110549 -22.0  17.00  
110550 -22.0  17.00  
110551 -22.0  17.00  
110552 -22.0  17.00  
110608 -22.0  17.00

In [264]:
pending3[pending3['ISO_country'].isnull()]

area_name  area_id  code_type  \
0                                              Castleford   118577        3.0   
1                                         Guminokiyokocho   118576        5.0   
2                                                 Linares   118575        3.0   
3                                               Greenford   118574        5.0   
4                                                Changshu   118573        3.0   
5                                              Litoměřice   118572        3.0   
6                                             Maglebrænde   118571        3.0   
7                                                Leordina   118570        3.0   
8                                                Kullamaa   118569        3.0   
9                                                  Simuna   118568        3.0   
10                                             Pontefract   118567        3.0   
11                                         Oron-le-Châtel   118566        4.0   
12                                               Netolice   118565        3.0   
13                                                Crimora   118564        3.0   
14                                              Karlskoga   118563        3.0   
15                                              Wakefield   118562        5.0   
16                                               Tebworth   118561        3.0   
17                                            Sanderstead   118560        5.0   
18                                            Zevenbergen   118559        3.0   
20                                    Montgomery Township   118557        4.0   
21                                                    Lar   118556        3.0   
22                                              Gushikawa   118555        3.0   
23                                            Shimabukuro   118554        5.0   
24                                              Bandhagen   118553        5.0   
25                                                 Weston   118552        5.0   
26                                                   York   118551        5.0   
27                                               Vineland   118550        5.0   
28                                                  Βόλος   118549        3.0   
29                                                Sidbury   118548        3.0   
30                                               McDonald   118547        3.0   
31                                                 Golden   118546        3.0   
32                                                Aliança   118544        4.0   
33                                                 Jarvis   118543        3.0   
34                                                Leksand   118542        3.0   
35                                                Guarana   118541        3.0   
36                                Saint-Jacques-le-Mineur   118539        3.0   
37      Les Jardins-de-Napierville Regional County Mun...   118538        4.0   
38                                                   Bise   118537        5.0   
39                                           Streekermoor   118535        3.0   
40                                             Neusüdende   118534        3.0   
41                                                Northam   118533        3.0   
42                                                Copiapó   118532        3.0   
43                                              Fort Kent   118531        3.0   
44                                                Coeburn   118530        3.0   
45                                                McClure   118529        3.0   
46                                               Canarsie   118528        5.0   
47                                                Whitney   118527        3.0   
48                               Saint-Gabriel-de-Brandon   118526        4.0   
49                                               Lievegem   118525        4.0  

The above areas haven't been identified, so we'll gather all the retrieved areas in one dataframe and start our next step.

In [269]:
retrieved_areas = pd.concat([retrieved, retrieved2, retrieved3, retrieved4], ignore_index=True)

### Selecting the origin for each release/artist

As we mentioned before, our objective is to retrieve, for each release, the origin of the artist who first released it. We would like to retrieve mainly their country, except for the US, where we'd like the state too.

To do so, we'll use the columns start_area1 first and our retrieved_areas dataframe.

In [271]:
df3.head()

release_id            release_group  credit_id  group_id  release_country  \
0     2163750                             2205562   1962329            240.0   
1     1846605                             1503027   1713833            240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358             73.0   
3     2265346                    Le 1     2291833   2042812            240.0   
4     1895266   M2Music HitDisc Vol. 1          1   1751021            222.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2018-01-01  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755   
4   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   

     artist_name_x  start_area1  start_area2  
0         Soul Glo       7707.0          NaN  
1      Ben Bennett          NaN          NaN  
2  Soixante Étages          NaN          NaN  
3         TedeuzeM      68613.0          NaN  
4  Various Artists          NaN          NaN

In [274]:
#Add the areas information to our main dataframe for the column "start_area_1":
df4 = pd.merge(df3, retrieved_areas, how='left', left_on='start_area1', right_on='area_id')
df4.head()

release_id            release_group  credit_id  group_id  release_country  \
0     2163750                             2205562   1962329            240.0   
1     1846605                             1503027   1713833            240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358             73.0   
3     2265346                    Le 1     2291833   2042812            240.0   
4     1895266   M2Music HitDisc Vol. 1          1   1751021            222.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2018-01-01  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755   
4   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   

     artist_name_x  start_area1  start_area2 ISO_code ISO_country  area_id  \
0         Soul Glo       7707.0          NaN      NaN         NaN      NaN   
1      Ben Bennett          NaN          NaN      NaN         NaN      NaN   
2  Soixante Étages          NaN          NaN      NaN         NaN      NaN   
3         TedeuzeM      68613.0          NaN      NaN          FR  68613.0   
4  Various Artists          NaN          NaN      NaN         NaN      NaN   

         area_name  code_type   lat  long subdivision  
0              NaN        NaN   NaN   NaN         NaN  
1              NaN        NaN   NaN   NaN         NaN  
2              NaN        NaN   NaN   NaN         NaN  
3  Aix-en-Provence        3.0  46.0   2.0         NaN  
4              NaN        NaN   NaN   NaN         NaN

In [275]:
#We save the rows for which we retrieved the coordinates:
release_retrieved = df4[df4['lat'].notnull()]

In [276]:
#How much information did we retrieve in this first step?
len(release_retrieved)

1016128

In [277]:
len(df4)

1499614

We just retrieved 68% of our data with this first attempt. We will now look into start_area2 to see if it provides us with more information.

Before that, we delete the last columns to avoid confusion.

In [280]:
release_pending = df4[df4['lat'].isnull()]
columns = ['ISO_code','ISO_country', 'area_id', 'area_name', 'code_type', 'lat', 'long','subdivision']
release_pending.drop(labels=columns, axis=1, inplace=True)

In [283]:
df5 = pd.merge(release_pending, retrieved_areas, how='left', left_on='start_area2', right_on='area_id')

In [284]:
#We save the rows for which we retrieved the coordinates:
release_retrieved2 = df5[df5['lat'].notnull()]

In [285]:
#How much information did we retrieve here?
len(release_retrieved2)

13677

In [287]:
#And how much do we have left?
release_pending2 = df5[df5['lat'].isnull()]
columns = ['ISO_code','ISO_country', 'area_id', 'area_name', 'code_type', 'lat', 'long','subdivision']
release_pending2.drop(labels=columns, axis=1, inplace=True)
len(release_pending2)

469809

So far, we have retrieved the origin for 1.029.805 releases, which is 69% of our dataframe. We will try however to retrieve a bit more information from other sources.

### Data from the 1 million songs dataset

Between 2011 and 2012, there was a Music Information Retrieval challenge called "Million Song Dataset". The majority of the data contained was provided by The Echo Nest (today known as Spotify).

At the bottom of the following website, there are links to download the Dataset:

https://labrosa.ee.columbia.edu/millionsong/pages/getting-dataset

As we won't use the whole dataset (just some of the tables), you don't need to download them: they will be attached in the repo.

In [288]:
artists_locations = pd.read_csv('1M_songs/artist_location.csv',sep='<SEP>', header=None, engine='python')
artists_locations.columns = ['artist_id','lat','long','artist_name','location_name']
artists_locations.head()

artist_id       lat      long           artist_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
1  AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
2  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
3  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
4  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                location_name  
0                  Santa Cruz  
1             Twin Cities, MN  
2  Harrow, Middlesex, England  
3           Richmond Hill, NY  
4                 Mississauga

In [289]:
#How many artist are there?
artists_locations['artist_id'].nunique()

13850

In this dataset, there is also another table which provides us with some extra information, especially the artist Musicbrainz's id (which will be very helpful to make the link with our main dataframe later).

In [290]:
metadata = pd.read_csv('1M_songs/track_metadata.csv',sep=',', header=0, engine='python', usecols=['artist_id','artist_mbid'])
metadata.head()

artist_id                           artist_mbid
0  ARYZTJS1187B98C555  357ff05d-848a-44cf-b608-cb34b5701ae5
1  ARMVN3U1187FB3A1EB  8d7ef530-a6fd-4f8f-b2e2-74aec765e0f9
2  ARGEKB01187FB50750  3d403d44-36ce-465c-ad43-ae877e65adc4
3  ARNWYLR1187B9B2F9C  12be7648-7094-495f-90e6-df4189d68615
4  AREQDTE1269FB37231                                   NaN

In [291]:
#We drop the rows withour artist_mbid (as we can't link them with our df)
metadata.dropna(subset=['artist_mbid'],axis=0, inplace=True)
#We merge artist_locations and metadata dataframes:
a = pd.merge(artists_locations,metadata,how='left',on='artist_id', copy=False)
a.dropna(subset=['artist_mbid'],axis=0, inplace=True)
a.head()

artist_id       lat      long   artist_name    location_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
1  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
2  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
3  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
4  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   

                            artist_mbid  
0  0bd9755c-c86d-431c-bc28-ef908b8a9821  
1  0bd9755c-c86d-431c-bc28-ef908b8a9821  
2  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
3  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
4  d4620364-82ec-4c34-9265-a2b72dfa8e3e

In [292]:
#We delete the useless columns:
a.drop(labels=['artist_id','artist_name'], axis=1, inplace=True)
#We get rid of the duplicate rows:
a.drop_duplicates(subset='artist_mbid', inplace=True)
a.head()

lat      long               location_name  \
0  -16.96595 -61.14804                  Santa Cruz   
2   46.44231 -93.36586             Twin Cities, MN   
33  51.59678  -0.33556  Harrow, Middlesex, England   
64  40.69626 -73.83301           Richmond Hill, NY   
78  43.58828 -79.64372                 Mississauga   

                             artist_mbid  
0   0bd9755c-c86d-431c-bc28-ef908b8a9821  
2   d4620364-82ec-4c34-9265-a2b72dfa8e3e  
33  e1079a78-75d4-4a1a-aef1-0be051386598  
64  4db4e744-3007-4386-b87d-9653acfe0464  
78  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8

Befor starting to retrieve geographical information about these artists, we need to know for which ones we don't already have the information in our main dataframe:

In [293]:
#Inner join to find the artist_mbid in common:
to_match = pd.merge(a, release_pending2[['artist_mbid']], how='inner', on='artist_mbid')
#Remove duplicates after merging:
to_match.drop_duplicates(subset=['artist_mbid'],keep='first', inplace=True)

In [295]:
to_match_list = to_match.artist_mbid.values.tolist()

In [296]:
to_match.artist_mbid.nunique()

1497

In [297]:
to_match.head()

lat       long    location_name                           artist_mbid
0  -16.96595  -61.14804       Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821
1   46.44231  -93.36586  Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e
7   34.05349 -118.24532  California - LA  8a9a5574-af01-455e-838f-5b4347bb28e7
9   60.39070    5.33275           Bergen  7a9e07cd-33bf-44b6-9479-884561fcc97a
15  42.50382   12.57347            ITALY  bdb2fe3b-1644-4418-a324-56c27939ac77

As we can see above, the column "location_name" provides us with some geographical information but, for instance, in the first row, we don't really know the country where Santa Cruz is located.

Luckily, we have a pair of coordinates that we can use to retrieve more geographical detail for each row, using our reverse_geocoder tool like we did before:

In [298]:
#We first create a new column called "coords" in which we'll gather both latitude and longitude:
to_match['coords'] = list(zip(to_match.lat, to_match.long))
coords = tuple(to_match['coords'].values.tolist())
#And now we use the reverse_geocoder utility to retrieve info for each pair of coordinates:
address = reverse_geocoder.search(coords)
to_match['address'] = address
to_match.head()

lat       long    location_name  \
0  -16.96595  -61.14804       Santa Cruz   
1   46.44231  -93.36586  Twin Cities, MN   
7   34.05349 -118.24532  California - LA   
9   60.39070    5.33275           Bergen   
15  42.50382   12.57347            ITALY   

                             artist_mbid  \
0   0bd9755c-c86d-431c-bc28-ef908b8a9821   
1   d4620364-82ec-4c34-9265-a2b72dfa8e3e   
7   8a9a5574-af01-455e-838f-5b4347bb28e7   
9   7a9e07cd-33bf-44b6-9479-884561fcc97a   
15  bdb2fe3b-1644-4418-a324-56c27939ac77   

                                       coords  \
0                      (-16.96595, -61.14804)   
1                       (46.44231, -93.36586)   
7   (34.053490000000004, -118.24531999999999)   
9                          (60.3907, 5.33275)   
15             (42.503820000000005, 12.57347)   

                                              address  
0   {'lat': '-16.43333', 'lon': '-60.9', 'name': '...  
1   {'lat': '46.53301', 'lon': '-93.71025', 'name'...  
7   {'lat': '34.05223', 'lon': '-118.24368', 'name...  
9   {'lat': '60.39299', 'lon': '5.32415', 'name': ...  
15  {'lat': '42.51956', 'lon': '12.52758', 'name':...

As we did before, we will retrieve the fields admin1 and cc for each row.

In [299]:
#We reset the index for the following loop to work:
to_match.reset_index(drop=True, inplace=True)

In [300]:
#We create 2 empty columns:
start = time.time()
to_match['state'] = np.nan
to_match['country_ISO'] = np.nan

#And fill them with the info we need:

for i in tqdm.tqdm(range(len(to_match))):
    address = list(to_match['address'][i].items())
    to_match['state'][i] = address[3][1]
    to_match['country_ISO'][i] = address[5][1]

end = time.time()
print(end-start)
#We check the result:
to_match.head()

100%|██████████| 1497/1497 [05:13<00:00,  4.83it/s]

313.5845203399658


lat       long    location_name                           artist_mbid  \
0 -16.96595  -61.14804       Santa Cruz  0bd9755c-c86d-431c-bc28-ef908b8a9821   
1  46.44231  -93.36586  Twin Cities, MN  d4620364-82ec-4c34-9265-a2b72dfa8e3e   
2  34.05349 -118.24532  California - LA  8a9a5574-af01-455e-838f-5b4347bb28e7   
3  60.39070    5.33275           Bergen  7a9e07cd-33bf-44b6-9479-884561fcc97a   
4  42.50382   12.57347            ITALY  bdb2fe3b-1644-4418-a324-56c27939ac77   

                                      coords  \
0                     (-16.96595, -61.14804)   
1                      (46.44231, -93.36586)   
2  (34.053490000000004, -118.24531999999999)   
3                         (60.3907, 5.33275)   
4             (42.503820000000005, 12.57347)   

                                             address       state country_ISO  
0  {'lat': '-16.43333', 'lon': '-60.9', 'name': '...  Santa Cruz          BO  
1  {'lat': '46.53301', 'lon': '-93.71025', 'name'...   Minnesota          US  
2  {'lat': '34.05223', 'lon': '-118.24368', 'name...  California          US  
3  {'lat': '60.39299', 'lon': '5.32415', 'name': ...   Hordaland          NO  
4  {'lat': '42.51956', 'lon': '12.52758', 'name':...      Umbria          IT

In [301]:
#We drop the unnecessary columns:
to_match.drop(labels=['lat','long','coords','address', 'location_name'], axis=1, inplace=True)
to_match.head()

artist_mbid       state country_ISO
0  0bd9755c-c86d-431c-bc28-ef908b8a9821  Santa Cruz          BO
1  d4620364-82ec-4c34-9265-a2b72dfa8e3e   Minnesota          US
2  8a9a5574-af01-455e-838f-5b4347bb28e7  California          US
3  7a9e07cd-33bf-44b6-9479-884561fcc97a   Hordaland          NO
4  bdb2fe3b-1644-4418-a324-56c27939ac77      Umbria          IT

In [304]:
#We create a column that combines "state" and "country_ISO", to do the merging after:
to_match['check'] = to_match['state'] + to_match['country_ISO']
#We drop duplicates in case there are two identical "check" items:
to_match.drop_duplicates(subset='check', keep=False, inplace=True)
to_match.head()

artist_mbid         state country_ISO  \
0   0bd9755c-c86d-431c-bc28-ef908b8a9821    Santa Cruz          BO   
38  34d42823-6b56-4861-a675-1565bf40d557        Saxony          DE   
48  d10d6fe4-4aea-476c-a84e-5e8868d2f037      Shizuoka          JP   
77  bc30924c-1900-41c3-9a97-41a93433836f      Adamaoua          CM   
84  ce762a8f-029b-4164-a341-405a0140945e  Metro Manila          PH   

             check  
0     Santa CruzBO  
38        SaxonyDE  
48      ShizuokaJP  
77      AdamaouaCM  
84  Metro ManilaPH

In [305]:
#Then, we create another "check" column in our retrieved_areas dataframe:
retrieved_copy = retrieved_areas.copy()
retrieved_copy['check'] = retrieved_copy['area_name'] + retrieved_copy['ISO_country']
#We drop duplicates in case there are two identical "check" items:
retrieved_copy.drop_duplicates(subset='check', keep=False, inplace=True)

In [317]:
#And we merge both dataframes using that column:
matched = pd.merge(to_match, retrieved_copy, how='left', on='check')
matched.head()

artist_mbid         state country_ISO  \
0  0bd9755c-c86d-431c-bc28-ef908b8a9821    Santa Cruz          BO   
1  34d42823-6b56-4861-a675-1565bf40d557        Saxony          DE   
2  d10d6fe4-4aea-476c-a84e-5e8868d2f037      Shizuoka          JP   
3  bc30924c-1900-41c3-9a97-41a93433836f      Adamaoua          CM   
4  ce762a8f-029b-4164-a341-405a0140945e  Metro Manila          PH   

            check ISO_code ISO_country  area_id   area_name  code_type   lat  \
0    Santa CruzBO     BO-S          BO    977.0  Santa Cruz        2.0 -17.0   
1        SaxonyDE      NaN         NaN      NaN         NaN        NaN   NaN   
2      ShizuokaJP      NaN         NaN      NaN         NaN        NaN   NaN   
3      AdamaouaCM    CM-AD          CM   3238.0    Adamaoua        2.0   6.0   
4  Metro ManilaPH      NaN         NaN      NaN         NaN        NaN   NaN   

   long subdivision  
0 -65.0         NaN  
1   NaN         NaN  
2   NaN         NaN  
3  12.0         NaN  
4   NaN         NaN

In [318]:
#We can now drop the columns that don't have any coordinates before mergin with our pending 2 dataframe:
matched.dropna(subset=['lat'], axis=0, inplace=True) 

In [319]:
#We input the retrieved information into our main dataframe:
matched.drop(labels=['state', 'check', 'country_ISO'], axis=1, inplace=True)
df6 = pd.merge(release_pending2, matched, how='left', on='artist_mbid')
df6.head()

release_id            release_group  credit_id  group_id  release_country  \
0     2163750                             2205562   1962329            240.0   
1     1846605                             1503027   1713833            240.0   
2     1714060    Beaux Soirs De Paris     1324142   1609358             73.0   
3     1895266   M2Music HitDisc Vol. 1          1   1751021            222.0   
4     1494610                        !    1367808   1435283            107.0   

  release_year  artist_id                           artist_mbid  \
0   2014-01-01  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a   
1   2015-01-01  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
2   1995-01-01  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
3   2006-01-01        1.0  89ad4ac3-39f7-470e-963a-56509c546377   
4   2006-01-01  1154943.0  2b0e7ee2-a1d0-45d9-9291-2d269bea9160   

     artist_name_x  start_area1  start_area2 ISO_code ISO_country  area_id  \
0         Soul Glo       7707.0          NaN      NaN         NaN      NaN   
1      Ben Bennett          NaN          NaN      NaN         NaN      NaN   
2  Soixante Étages          NaN          NaN      NaN         NaN      NaN   
3  Various Artists          NaN          NaN      NaN         NaN      NaN   
4          三田村管打団?          NaN          NaN      NaN         NaN      NaN   

  area_name  code_type  lat  long subdivision  
0       NaN        NaN  NaN   NaN         NaN  
1       NaN        NaN  NaN   NaN         NaN  
2       NaN        NaN  NaN   NaN         NaN  
3       NaN        NaN  NaN   NaN         NaN  
4       NaN        NaN  NaN   NaN         NaN

In [320]:
#We save the rows for which we retrieved the coordinates:
release_retrieved3 = df6[df6['lat'].notnull()]

In [321]:
#How much information did we retrieve here?
len(release_retrieved3)

1487

In [322]:
#And how much do we have left?
release_pending3 = df6[df6['lat'].isnull()]
columns = ['ISO_code','ISO_country', 'area_id', 'area_name', 'code_type', 'lat', 'long','subdivision']
release_pending3.drop(labels=columns, axis=1, inplace=True)
len(release_pending3)

468322

### Data from Wikidata Query with SPARQL

https://query.wikidata.org/

1) Musicians

SELECT ?musician ?musicianLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?place_of_birth ?place_of_birthLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?musician wdt:P106 wd:Q639669.
  OPTIONAL { ?musician wdt:P136 ?genre. }
  OPTIONAL { ?musician wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?musician wdt:P19 ?place_of_birth. }
}


--> Export to csv file: query_wikidata_musicians.csv

2) Singers

SELECT ?musician ?musicianLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?place_of_birth ?place_of_birthLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?musician wdt:P106 wd:Q177220.
  OPTIONAL { ?musician wdt:P136 ?genre. }
  OPTIONAL { ?musician wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?musician wdt:P19 ?place_of_birth. }
}

--> Export to csv file: query_wikidata_singers.csv

3) Bands

SELECT ?band ?bandLabel ?genre ?genreLabel ?MusicBrainz_artist_ID ?location_of_formation ?location_of_formationLabel WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "[AUTO_LANGUAGE],en". }
  ?band wdt:P31 wd:Q215380.
  OPTIONAL { ?band wdt:P136 ?genre. }
  OPTIONAL { ?band wdt:P434 ?MusicBrainz_artist_ID. }
  OPTIONAL { ?band wdt:P740 ?location_of_formation. }
}

--> Export to csv file: query_wikidata_bands.csv

In [323]:
#Open the files and load them into dataframes with the same column names (to match with our main dataframe later):
musicians = pd.read_csv('wikidata/query_wikidata_musicians.csv',sep=',', encoding='utf-8', usecols=[4,6])
musicians.rename(columns={'MusicBrainz_artist_ID':'artist_mbid','place_of_birthLabel':'origin_name'}, inplace=True)
singers = pd.read_csv('wikidata/query_wikidata_singers.csv',sep=',', encoding='utf-8', usecols=[4,6])
singers.rename(columns={'MusicBrainz_artist_ID':'artist_mbid','place_of_birthLabel':'origin_name'}, inplace=True)
bands = pd.read_csv('wikidata/query_wikidata_bands.csv',sep=',', encoding='utf-8', usecols=[4,6])
bands.rename(columns={'MusicBrainz_artist_ID':'artist_mbid','location_of_formationLabel':'origin_name'}, inplace=True)

In [324]:
bands.head()

artist_mbid origin_name
0  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
1  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
2  f26c72d3-e52c-467b-b651-679c73d8e1a7  Sacramento
3  a3cb23fc-acd3-4ce0-8f36-1e5aa6a18432      Dublin
4  a3cb23fc-acd3-4ce0-8f36-1e5aa6a18432      Dublin

In [325]:
#Now we can concatenate the 3 dataframes into one:
wiki_df = pd.concat([musicians, singers, bands])
wiki_df.head()

artist_mbid            origin_name
0                                   NaN  Cherbourg-en-Cotentin
1  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
2  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
3  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg
4  b972f589-fb0e-474e-b64a-803b0364fa75               Salzburg

In [326]:
#We can directly drop the rows which don't have a musicbrainz's id (we need and ID to join with our main df):
wiki_df.dropna(subset=['artist_mbid'], axis=0, inplace=True)

In [327]:
len(wiki_df)

116020

In [328]:
#Let's see how many artists we have:
wiki_df['artist_mbid'].nunique()

96110

In [329]:
#Drop duplicated artist_mbid:
wiki_df.drop_duplicates(subset=['artist_mbid'],keep='first', inplace=True)

In [330]:
#What kind of information do we have in the column origin_name?:
wiki_df.origin_name.value_counts()

New York City                           1273
Los Angeles                             1209
London                                   995
Tokyo                                    750
Paris                                    440
Chicago                                  436
Brooklyn                                 390
Seoul                                    376
Philadelphia                             348
Toronto                                  333
Berlin                                   324
Stockholm                                323
San Francisco                            289
Seattle                                  282
Boston                                   268
Moscow                                   267
California                               266
Detroit                                  248
Montreal                                 248
Oslo                                     219
Rome                                     215
Helsinki                                 212
Rio de Jan

In [331]:
wiki_df.head()

artist_mbid  origin_name
1   b972f589-fb0e-474e-b64a-803b0364fa75     Salzburg
12  b58165ba-ac55-49a1-8855-caf16c68f5f2         Sète
13  d135874d-9cae-4fef-97e3-36acbd9f5a26      Chicago
14  75167b8b-44e4-407b-9d35-effe87b223cf      Toronto
24  4b585938-f271-45e2-b19a-91c634b5e396  Bexleyheath

It looks like we have city names, so we can use our retrieved_areas dataframe to match by area_name. However, we'll have to drop duplicates in both retrieved areas and wiki_df, to avoid mismatching.

In [332]:
#We first delete the duplicate area names in our wiki_df:
wiki_df.drop_duplicates(subset='origin_name', keep=False, inplace=True)
#We do the same with our retrieved_areas dataframe:
areas_dedup = retrieved_areas.drop_duplicates(subset='area_name', keep=False)

In [333]:
#Now we can merge wiki_df with areas_dedup:
retrieved_wiki = pd.merge(wiki_df, areas_dedup, how='left', left_on='origin_name', right_on='area_name')
retrieved_wiki.head()

artist_mbid    origin_name ISO_code ISO_country  \
0  4b585938-f271-45e2-b19a-91c634b5e396    Bexleyheath      NaN         NaN   
1  dc0640db-f5db-4fde-a5ca-ab1331f94a43       Anchiano      NaN         NaN   
2  6fdd3b3e-1ea6-4da9-8d6f-8f8de01c133a        Ciboure      NaN         NaN   
3  09ff1fe8-d61c-4b98-bb82-18487c74d7b7  Żelazowa Wola      NaN         NaN   
4  2a33d974-ad9e-4b51-917e-fb9397bf82c6    Puente Alto      NaN         NaN   

   area_id area_name  code_type  lat  long subdivision  
0      NaN       NaN        NaN  NaN   NaN         NaN  
1      NaN       NaN        NaN  NaN   NaN         NaN  
2      NaN       NaN        NaN  NaN   NaN         NaN  
3      NaN       NaN        NaN  NaN   NaN         NaN  
4      NaN       NaN        NaN  NaN   NaN         NaN

In [334]:
retrieved_wiki.ISO_country.isnull().value_counts()

True     6225
False     957
Name: ISO_country, dtype: int64

We just retrieved the origin 957 artists which we didn't have before. Let's input this information into our main dataframe and see how many releases they represent.

In [335]:
#And we can merge that information into our main dataframe:
df7 = pd.merge(release_pending3, retrieved_wiki, how='left', on='artist_mbid')
df7.columns

Index(['release_id', 'release_group', 'credit_id', 'group_id',
       'release_country', 'release_year', 'artist_id', 'artist_mbid',
       'artist_name_x', 'start_area1', 'start_area2', 'origin_name',
       'ISO_code', 'ISO_country', 'area_id', 'area_name', 'code_type', 'lat',
       'long', 'subdivision'],
      dtype='object')

In [336]:
#We save the rows for which we retrieved the coordinates:
release_retrieved4 = df7[df7['lat'].notnull()]

In [337]:
#How much information did we retrieve here?
len(release_retrieved4)

131

In [338]:
#And how much do we have left?
release_pending4 = df7[df7['lat'].isnull()]
columns = ['ISO_code','ISO_country', 'area_id', 'area_name', 'code_type', 'lat', 'long','subdivision', 'origin_name']
release_pending4.drop(labels=columns, axis=1, inplace=True)
len(release_pending3)

468322

We have retrieved the information for an extra 131 releases in this last step, thanks to Wikidata Query.

As we have retrieved geographical data from 4 different sources already, we need to analyze what we have left and decide what to do.

Who are the artists for which we don't have any origin information?

In [342]:
#How many artists are there?
release_pending4['artist_mbid'].nunique()

169087

So, according to the above line, we have 169.087 artists with unknown or vague origin. Let's have a closer look:

In [344]:
unknown_artist = release_pending4.groupby('artist_name_x').count().sort_values('release_id',ascending=False)
unknown_artist.head(1000)

release_id  release_group  \
artist_name_x                                                                   
Various Artists                                         134847         134847   
[language instruction]                                     278            278   
Little Richard                                             193            193   
Dwelling of Duels                                          180            180   
[nature sounds]                                            170            170   
Dream Theater                                              143            143   
Peerless Orchestra                                         122            122   
Daniel Menche                                              115            115   
Edison Concert Band                                        115            115   
Minniva                                                    114            114   
[dialogue]                                                 112            112   
Bibi & Tina                                                109            109   
Eminem                                                     108            108   
[no artist]                                                108            108   
Ike & Tina Turner                                          102            102   
HasenChat Music                                            100            100   
How Did This Get Made?                                      98             98   
Edward M. Favor                                             97             97   
Samuel Sagan                                                95             95   
Jonathan Parecki                                            94             94   
Meat Loaf                                                   93             93   
Tim Timebomb                                                90             90   
Les Schtroumpfs                                             89             89   
Dan W. Quinn                                                86             86   
Gucci Mane                                                  83             83   
Diverse System                                              82             82   
Nas                                                         79             79   
Dead Eye Darter                                             74             74   
Marc Gruppe                                                 73             73   
OverClocked ReMix                                           72             72   
Night Vale Presents                                         72             72   
Two Steps From Hell                                         71             71   
[christmas music]                                           71             71   
Armand van Helden                                           70             70   
Edward Ka-Spel                                              70             70   
Chxpo                                                       69             69   
Detroit Symphony Orchestra                                  69             69   
Qumu                                                        68             68   
Los Tigres del Norte                                        68             68   
Harry Anthony                                               67             67   
Brandon Fiechter                                            66             66   
Alstroemeria Records                                        66             66   
John Cale                                                   66             66   
Benjamin Blümchen                                           65             65   
audiomachine                                                65             65   
Futuramerlin.com                                            65             65   
waterfront dining                                           64             64   
Kidz Bop                                                    64             64   
Ed

In [346]:
#From what we can see above, the category "Various Artists" has many releases assigned:
release_pending4[release_pending4['artist_name_x']=='Various Artists']

release_id                                      release_group  \
3          1895266                             M2Music HitDisc Vol. 1   
9           356044                        !!!Here Ain't the Sonics!!!   
14         1623578                                            !Go Hit   
15          475440                        !JBL, Volume 2: PROGRESSIVE   
16           62055                                                !K7   
17         1053661                                   !K7 2011 Sampler   
18           62061                                    !K7 Compilation   
19         1447852                                    !K7 Compilation   
20         1012140                                    !K7 Spring 2002   
21         2319247                          !Kollections 02: Classics   
22         2327624                              !Kollections 07: 2018   
24          725914                          !Mpact 3 Jump & Hardstyle   
28          686550                          !mpact (Jump & Hardstyle)   
29         1630852                   !mpact Part 2 (Jump & Hardstyle)   
36         1572461         # Flashback: The House Classics Collection   
76          510871          #1 Club Hits 2008: Best of Dance & Techno   
77         2241261         #1 Club Hits 2010 - Best of Dance & Techno   
78         1582410  #1 Club Hits Vol. 1: Best of Dance & Techno Ed...   
79         1766351               #1 Club Hits: Best of Dance & Techno   
85         1350888                                            #1 Hits   
86          178590                                  #1 Hits 1980-1984   
87          402912                                 #1 Hits Love Songs   
88         1766782             #1 Hits of Disco: The Original Masters   
89          404062                                #1 Hits of the '80s   
90          412730                           #1 Hits of the 50s & 60s   
91          117141      #1 Hits of the 50s (The Pure Gold Collection)   
92         1563701                      #1 Hits of the 50s Volume Two   
93         1563690                     #1 Hits of the 50s, Volume One   
94          127131                                 #1 Hits of the 60s   
95          597713                                #1 Hits of the 70's   
96         1489657                                 #1 Hits of the 70s   
97           27281                                 #1 Hits of the 80s   
98          804099                       #1 Hits of the 90's (disc 2)   
99          616073                             #1 Hits of the Sixties   
100         175209                               #1 Hits: 1970 - 1974   
101         558349                               #1 Hits: 1985 - 1989   
102         718542                     #1 Hits: Best of 80s Hit Radio   
103         170562                          #1 Hits: Classic 80s Rock   
104        1079850                           #1 Love Songs of the 70s   
105         192133                       #1 Pop Hits of the 60s & 70s   
107        1859994                   #1 Reason to Move to Gainesville   
108         643165                                #1 Smooth Love Hits   
109         266373  #1 Soul Hits of the 60s, Volume 3: A Brand New...   
110         643163                                  #1 Super 80s Hits   
111        2158299                         #1 Super Country 80’s Hits   
115        2142036                 #100: Great Tunes From Scandinavia   
116        2136733                          #11 Wecord: Wootball 2014   
118        2154803                           #14 Wecord: Cool as Duck   
122         695486                                        #1s Ghazals   
123         815395                      #1s The Greatest Bhangra Hits   
124         494614     #1s: 38 of the Greatest #1 Singles of All Time   
125         494615  #1s: 38 of the Greatest #1 Singles of All Time...   
177        1696475                            #BowTieWednesday Vol. 5   
179        1244270                            #CC-10 Birthday Mixt

If we look in detail into these releases, we can see that most of them are music compilations (hence the generic category "Various Artists"). As they are music compilations, that means that the tracks included were originally released before by their genuine author, so we shouldn't take them into account. Also, as we don't have an artist name for them, it will be impossible to retrieve the origin.

We will delete those rows from our dataframe later.

Let's analyze more in detail who are the rest of artists that have many releases, and decide what to do with them.

In [348]:
#"Language instruction" artist:
release_pending4[release_pending4['artist_name_x']=='[language instruction]']

release_id                                      release_group  \
4058        821781                                   15 Minute French   
4059        822699                                  15 Minute Italian   
9399        536732     450 Nouveaux Exercices Grammaire Niveau Avancé   
16550      1921485                              A break in/The Police   
16723      1920797                             A new telephone number   
23955      2107126      All Audio Spanish - Basic-Intermediate Disc 1   
25291       685879                                  All-Audio Spanish   
26350      1381788                                        Alter ego 2   
26490      1921562                        Alternative forms of energy   
32088      1921270                              Apologies and excuses   
32648       630154                            Arabic: Advanced Course   
32649       630138                          Arabic: Foundation Course   
32650      1228950                                 Arabic: Vocabulary   
33226      1921572                     Arguing over Grades/Profession   
33227      1921489                               Arguing over a party   
35570      1921584                                       At the Metro   
35586      1920817                              At the Police Station   
35618      1920800                                         At the bar   
35619      1920798                                   At the bookstore   
35620      1920805                                    At the bus stop   
35621      1920475                                      At the cinema   
35622      1921491           At the cosmetics store/At the jeweller's   
35623      1921552                                   At the dietician   
35624      1920804                                    At the doctor's   
35625      1920818                               At the hairdresser's   
35626      1920814                                    At the hospital   
35627      1920802                                       At the hotel   
35628      1920480                                       At the kiosk   
35629      1920451                                       At the party   
35630      1920481                                 At the post office   
35631      1920469                                       At the store   
35632      1920811           At the super market/At the street market   
35633      1920497         At the super market/at the open-air market   
35635      1920786                               At the travel office   
35636      1921267             At the video store/At the record store   
39629      2014765                       Baby's First Steps in French   
39630      2014773                      Baby's First Steps in Spanish   
39631       475724                       Baby's First Words in French   
39632       478425                      Baby's First Words in Italian   
43136       424205                             Basic Business Chinese   
47044       500267                   Berlitz Japanese Phrasebook & CD   
47045      1666738                       Berlitz: Turkish Travel Pack   
48381      1856198                     Beste Freunde A 1.1 - Kursbuch   
48976      1921581                                 Beware of the sun!   
56540       361228         Bonne Route! Students' Listening Exercises   
59430      1921576                                          Break-ins   
74878      1920792                                     Cinema tickets   
77165      1921582                                     Climate change   
80965      1920472                                           Commands   
82399      1920815                       Congratulations and sympathy   
90511      1921543               Damages in the house/The electrician   
90512      1920824                   Damages in the house/The plumber   
100143      677095          Der neue Hörkurs: Französisch ganz leicht   
101403      798635            Deutsch in 30 Tagen – German in 30 D

As its name suggests, these releases are language courses recorded, so they are not music and they are out of our scope too.

The same would apply to the categories [nature sounds], [dialogue], [christmas music], [no artist] and [church chimes].

We can now delete from our dataframes all these cathegories, and see what we have left.

In [349]:
#In our main dataframe:
labels = ['[nature sounds]','[dialogue]','[christmas music]', '[no artist]', '[church chimes]','Various Artists','[language instruction]']
release_pending4.drop(release_pending4[release_pending4['artist_name_x'].isin(labels)].index, axis=0, inplace=True)

In [350]:
#So after this deletion of some releases, how many do we have left to retrieve the origin?
len(release_pending4)

332550

In [351]:
#Wich are the unknow artists that produce the most releases?
unknown = release_pending4.groupby(by='artist_name_x', axis=0).count()
unknown.sort_values(by='release_id',axis=0, ascending=False)

release_id  release_group  \
artist_name_x                                                                   
Little Richard                                             193            193   
Dwelling of Duels                                          180            180   
Dream Theater                                              143            143   
Peerless Orchestra                                         122            122   
Daniel Menche                                              115            115   
Edison Concert Band                                        115            115   
Minniva                                                    114            114   
Bibi & Tina                                                109            109   
Eminem                                                     108            108   
Ike & Tina Turner                                          102            102   
HasenChat Music                                            100            100   
How Did This Get Made?                                      98             98   
Edward M. Favor                                             97             97   
Samuel Sagan                                                95             95   
Jonathan Parecki                                            94             94   
Meat Loaf                                                   93             93   
Tim Timebomb                                                90             90   
Les Schtroumpfs                                             89             89   
Dan W. Quinn                                                86             86   
Gucci Mane                                                  83             83   
Diverse System                                              82             82   
Nas                                                         79             79   
Dead Eye Darter                                             74             74   
Marc Gruppe                                                 73             73   
OverClocked ReMix                                           72             72   
Night Vale Presents                                         72             72   
Two Steps From Hell                                         71             71   
Armand van Helden                                           70             70   
Edward Ka-Spel                                              70             70   
Detroit Symphony Orchestra                                  69             69   
Chxpo                                                       69             69   
Los Tigres del Norte                                        68             68   
Qumu                                                        68             68   
Harry Anthony                                               67             67   
Brandon Fiechter                                            66             66   
John Cale                                                   66             66   
Alstroemeria Records                                        66             66   
Benjamin Blümchen                                           65             65   
Futuramerlin.com                                            65             65   
audiomachine                                                65             65   
Kidz Bop                                                    64             64   
waterfront dining                                           64             64   
Radio Massacre International                                62             62   
Edison Grand Concert Band                                   62             62   
Melbourne Ska Orchestra                                     61             61   
The 16-Bit Audiophile Project                               61             61   
Carbon Leaf                                                 60             60   
Rebecca Sheir                                               59             59   
Br

We can immediately spot a few well known artists in the above list.

It could be an idea to retrieve information for the remaining artists by searching into Wikipedia online, however, we will leave this task as a bonus point for later if we have time.

For now, we will consider that, for these releases whose artists' origin hasn't been identified yet, their origin is equal to their release area (ie: the area in which they were produced). We will have to fill in the origin columns with the release_area info.

In [362]:
unknown.to_csv('unknown_artist_origin.csv', sep='\t', index=False, encoding='utf-8')

In [365]:
#We do the merging by the release country to extract its details:
df8 = pd.merge(release_pending4, retrieved_areas, how='left', left_on='release_country', right_on='area_id')

In [366]:
#We save the rows for which we retrieved the coordinates:
release_retrieved5 = df8[df8['lat'].notnull()]

In [367]:
#How much information did we retrieve here?
len(release_retrieved5)

250747

In [368]:
#And how much do we have left?
release_pending5 = df8[df8['lat'].isnull()]
columns = ['ISO_code','ISO_country', 'area_id', 'area_name', 'code_type', 'lat', 'long','subdivision', 'origin_name']
release_pending5.drop(labels=columns, axis=1, inplace=True)
len(release_pending5)

81803

We can see that this last step has provided us with information for 250.747 releases, which leaves us with 94% of our dataframe completed (as far as the geographical origin is concerned).

We'll now export our main dataframe as the result of this Notebook and we'll follow-up in the next one called "Data_gathering_music_genre":

In [373]:
data_out = pd.concat([all_rel, release_retrieved5], ignore_index=True)
data_out.isnull().any()

ISO_code            True
ISO_country        False
area_id            False
area_name          False
artist_id           True
artist_mbid         True
artist_name_x       True
code_type          False
credit_id          False
group_id           False
lat                False
long               False
origin_name         True
release_country    False
release_group       True
release_id         False
release_year       False
start_area1         True
start_area2         True
subdivision         True
dtype: bool

In [374]:
len(data_out)

1282170

In [375]:
data_out.duplicated(subset='release_id').any()

False

In [377]:
#Drop unnecesary columns:
to_drop = ['code_type', 'origin_name', 'release_country', 'start_area1', 'start_area2', 'subdivision']
data_out.drop(labels=to_drop, axis=1, inplace=True)

In [381]:
#Ordering the columns for better visibility:
order = ['release_id','release_group', 'group_id','release_year','artist_id','artist_mbid', 'credit_id','artist_name_x','area_id', 'area_name','ISO_code', 'ISO_country', 'lat', 'long']
final = data_out.reindex(columns=order)

In [383]:
final.to_csv('Dataframe_with_origin.csv', sep='\t', index=False, encoding='utf-8')